# Capstone Project - The Battle of the Neighborhoods
### By Altaf Jamalia

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)





## Introduction: Business Problem <a name="introduction"></a>

Mr.John currently stays in **Downtown Toronto** with his family and now has a good job opportunity in the **United States of America**. He needs to move to **New York City** with his family.

Mr.John has never been to New York City and is looking to us to help him find a **good location within New York for him and his family to settle down**. Mr.John and his family are accustomed to the busy downtown life with good options and is looking for a similar location in New York.

We will use Data Science to generate a few most promising neighborhoods based on this criteria so that Mr.John can take an informed decision and move to New York, USA. 

## Data <a name="data"></a>

Mr.John has made it clear that his family enjoys the Downtown life, so based on this criteria, we are going look at the locations in New York which has:
* Good Downtown neighborhood that has good Options in Restaurants (any type of restaurant), Shopping, Schooling 

Following data sources will be needed to extract/generate the required information:
* New York Neighborhood data available from ** https://cocl.us/new_york_dataset**
* Restaurants and their type, Shopping, Schools and other venues in the neighborhoods of New York will be obtained using **Foursquare API**
* Coordinates of New York and the Boroughs in New York will be obtained using **Google Maps API geocoding** 

### Explore the New York Neighborhood dataset

Lets first download the New York Neighborhood dataset and understand the Boroughs and Neighborhood.

Importing all the required libraries for the exploratory data analysis

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
!pip install folium
import folium # map rendering library

print('Libraries imported.')

     |████████████████████████████████| 92kB 6.0MB/s eta 0:00:011
Libraries imported.


In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

All the relevant data is in the features key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [4]:
neighborhoods_data = newyork_data['features']
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Transforming the data into a pandas dataframe

In [5]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Lets now fill this dataframe with the neighborhood_data 

In [6]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

neighborhoods.head                

<bound method NDFrame.head of            Borough               Neighborhood   Latitude  Longitude
0            Bronx                  Wakefield  40.894705 -73.847201
1            Bronx                 Co-op City  40.874294 -73.829939
2            Bronx                Eastchester  40.887556 -73.827806
3            Bronx                  Fieldston  40.895437 -73.905643
4            Bronx                  Riverdale  40.890834 -73.912585
5            Bronx                Kingsbridge  40.881687 -73.902818
6        Manhattan                Marble Hill  40.876551 -73.910660
7            Bronx                   Woodlawn  40.898273 -73.867315
8            Bronx                    Norwood  40.877224 -73.879391
9            Bronx             Williamsbridge  40.881039 -73.857446
10           Bronx                 Baychester  40.866858 -73.835798
11           Bronx             Pelham Parkway  40.857413 -73.854756
12           Bronx                City Island  40.847247 -73.786488
13           Bronx

Lets count how many boroughs and neighborhoods are there in this dataframe

In [7]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Now we need to get the latitude and longitude values of New York City using geopy library

In [8]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Lets use Folium to display a map of New York City and then super impose the neighborhoods from the dataframe "neighborhoods"

In [9]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Methodology <a name="methodology"></a>

The data shows us that there are 5 Boroughs in New York - 
**Manhattan** 
**Brooklyn**
**Bronx**
**Staten Island**
**Queens** 

Mr. John has not given any preference for any of the Boroughs, we are left with no other option but to do an analysis of all the Boroughs and its neighborhoods. Our approach will be as follows:

1. Do an analysis of one Borough and all its neighborhood at a time
2. Use FourSquare API to explore the neighborhood
3. Fetch the top 100 venues in a radius of 500 meters for each of these neighborhoods
4. Do an analysis and get the Top 10 most common venues in each of the neighborhoods
5. Use K-Means clustering to cluster the neighborhoods
6. The end result will be the clustered neighborhoods in that borough with the top 10 common venues in it

This will be repeated for all the Boroughs and its neighborhoods.

Mr.John's criteria was for a good neighborhood that has **good options in restaurants (any type), Shopping, Schools etc.**

**Once our analysis is complete, it will present a detailed view of all the neighborhoods in each Borough along with its most common venue. Based on this Mr.John will be able to make an informed decision of which Borough and neighborhood he would like to relocate to.**

**Lets start off with Manhattan and then go onto the other Boroughs**

## Analysis <a name="analysis"></a>

**Exploratory Data Analysis for each of the Boroughs and its neighborhoods starts here. The sequence of anaysis of the Boroughs and its neighborhoods is as follows**

1. Manhattan
2. Staten Island
3. Brooklyn
4. Bronx
5. Queens

In [10]:
CLIENT_ID = 'RLVWXTIGIRWG0XZR3TOBWSOX2W0APDZPDH22NM2PQQOH2BCZ' # your Foursquare ID
CLIENT_SECRET = '4MOV5BRCBDLV31LYBPGHGSH04EE3WEI3ANKQLUQOODBJBKUG' # your Foursquare Secret
VERSION = '20200101' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: RLVWXTIGIRWG0XZR3TOBWSOX2W0APDZPDH22NM2PQQOH2BCZ
CLIENT_SECRET:4MOV5BRCBDLV31LYBPGHGSH04EE3WEI3ANKQLUQOODBJBKUG


Lets now create a new Dataframe which has only Manhattan neighborhoods

In [11]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

Lets also get the Latitude and Longitude co-ordinates for Manhattan using the geopy library

In [12]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


A picture says a thousand words, so lets create a map using Folium and superimpose the manhattan data alone

In [13]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

Lets create a function to explore all the neighborhoods in all the Boroughs in Manhattan. 

We are going to get the Top 100 venues and within the radius of 500 meters in each neighborhood 

In [14]:
# type your answer here
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Now that the function is ready, lets extract the venues for each Borough and Neighborhood and store it in a new dataframe called **manhattan_venues**

In [64]:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


#### Lets check the size of this dataframe

In [65]:
print(manhattan_venues.shape)
manhattan_venues.head()

(2969, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066        Dunkin'   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877136       -73.906666     Donut Shop  
4       40.877531       -73.905582    Coffee Shop

Grouping the Venues by Neighborhood

In [66]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       56                      56     56   
Carnegie Hill                           88                      88     88   
Central Harlem                          44                      44     44   
Chelsea                                 99                      99     99   
Chinatown                              100                     100    100   
Civic Center                            90                      90     90   
Clinton                                100                     100    100   
East Harlem                             41                      41     41   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                                95                      95     95   
Gramercy                                69                      69     69   
Greenwich Village                      100                     100    100   
Hamilton Heights                        61                      61     61   
Hudson Yards                            52                      52     52   
Inwood                                  56                      56     56   
Lenox Hill                             100                     100    100   
Lincoln Square                          91                      91     91   
Little Italy                           100                     100    100   
Lower East Side                         40                      40     40   
Manhattan Valley                        37                      37     37   
Manhattanville                          44                      44     44   
Marble Hill                             25                      25     25   
Midtown                                100                     100    100   
Midtown South                           82                      82     82   
Morningside Heights                     39                      39     39   
Murray Hill                             75                      75     75   
Noho                                    99                      99     99   
Roosevelt Island                        28                      28     28   
Soho                                    65                      65     65   
Stuyvesant Town                         17                      17     17   
Sutton Place                            88                      88     88   
Tribeca                                 74                      74     74   
Tudor City                              73                      73     73   
Turtle Bay                             100                     100    100   
Upper East Side                         87                      87     87   
Upper West Side                         63                      63     63   
Washington Heights                      91                      91     91   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                56               56              56  
Carnegie Hill                    88               88              88  
Central Harlem                   44               44              44  
Chelsea                          99               99              99  
Chinatown                       100              100             100  
Civic Center                     90               90              90  
Clinton                         100              100             100  
East Harlem                      41               41              41  
East Village                    100              100             100  
Finan

In [67]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 320 uniques categories.


#### Lets analyze each neighborhood in Manhattan

In [68]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Marble Hill                  0               0                  0   
1  Marble Hill                  0               0                  0   
2  Marble Hill                  0               0                  0   
3  Marble Hill                  0               0                  0   
4  Marble Hill                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  BBQ Joint  Baby Store  \
0                      0                    0          0           0   
1                      0                    0          0           0   
2                      0                    0          0           0   
3                      0                    0          0           0   
4                      0                    0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Stadium  Beer Bar  Beer Garden  Beer Store  \
0                   0         0            0           0   
1                   0         0            0           0   
2                   0         0            0           0   
3                   0         0            0           0   
4                   0         0            0           0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   Breakfast Spot  Bridal Shop  Bridge  Bubble Tea Shop  Building  \
0               0            0       0                0         0   
1               0    

In [69]:
manhattan_onehot.shape

(2969, 321)

#### Lets group the rows by Neighborhood and by taking the mean of the frequency of occurance of each category

In [70]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000        0.000000               0.00   
1         Carnegie Hill           0.000000        0.000000               0.00   
2        Central Harlem           0.000000        0.000000               0.00   
3               Chelsea           0.000000        0.000000               0.00   
4             Chinatown           0.000000        0.000000               0.00   
5          Civic Center           0.000000        0.000000               0.00   
6               Clinton           0.000000        0.000000               0.00   
7           East Harlem           0.000000        0.000000               0.00   
8          East Village           0.000000        0.000000               0.00   
9    Financial District           0.000000        0.000000               0.00   
10             Flatiron           0.000000        0.000000               0.00   
11             Gramercy           0.000000        0.000000               0.00   
12    Greenwich Village           0.000000        0.000000               0.00   
13     Hamilton Heights           0.000000        0.000000               0.00   
14         Hudson Yards           0.000000        0.000000               0.00   
15               Inwood           0.000000        0.000000               0.00   
16           Lenox Hill           0.000000        0.000000               0.01   
17       Lincoln Square           0.010989        0.000000               0.00   
18         Little Italy           0.000000        0.000000               0.00   
19      Lower East Side           0.000000        0.000000               0.00   
20     Manhattan Valley           0.000000        0.000000               0.00   
21       Manhattanville           0.000000        0.000000               0.00   
22          Marble Hill           0.000000        0.000000               0.00   
23              Midtown           0.000000        0.000000               0.00   
24        Midtown South           0.000000        0.000000               0.00   
25  Morningside Heights           0.000000        0.000000               0.00   
26          Murray Hill           0.000000        0.000000               0.00   
27                 Noho           0.000000        0.000000               0.00   
28     Roosevelt Island           0.000000        0.000000               0.00   
29                 Soho           0.000000        0.000000               0.00   
30      Stuyvesant Town           0.000000        0.000000               0.00   
31         Sutton Place           0.000000        0.011364               0.00   
32              Tribeca           0.000000        0.000000               0.00   
33           Tudor City           0.000000        0.000000               0.00   
34           Turtle Bay           0.000000        0.000000               0.00   
35      Upper East Side           0.000000        0.000000               0.00   
36      Upper West Side           0.000000        0.000000               0.00   
37   Washington Heights           0.010989        0.000000               0.00   
38         West Village           0.000000        0.000000               0.00   
39            Yorkville           0.000000        0.000000               0.00   

    African Restaurant  American Restaurant  Antique Shop    Arcade  \
0             0.000000             0.000000      0.000000  0.000000   
1             0.000000             0.011364      0.000000  0.000000   
2             0.045455             0.045455      0.000000  0.000000   
3             0.000000             0.020202      0.000000  0.000000   
4             0.000000             0.030000      0.000000  0.000000   
5             0.000000             0.022222      0.011111  0.000000   
6             0.000000             0.030000      0.000000  0.000000   
7             0.000000             0.000000      0.000000  0.000000   
8             0.000000             0.010000      0

In [71]:
manhattan_grouped.shape

(40, 321)

#####  Printing each neighborhood along with the top 5 most common venues

In [72]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
           venue  freq
0           Park  0.11
1          Hotel  0.07
2            Gym  0.07
3  Memorial Site  0.05
4  Boat or Ferry  0.05


----Carnegie Hill----
                  venue  freq
0           Coffee Shop  0.09
1                  Café  0.05
2           Yoga Studio  0.03
3  Gym / Fitness Center  0.03
4             Bookstore  0.03


----Central Harlem----
                  venue  freq
0    Seafood Restaurant  0.05
1                   Bar  0.05
2  Gym / Fitness Center  0.05
3   Fried Chicken Joint  0.05
4     French Restaurant  0.05


----Chelsea----
                venue  freq
0         Art Gallery  0.16
1         Coffee Shop  0.07
2  Italian Restaurant  0.03
3  Seafood Restaurant  0.03
4      Ice Cream Shop  0.03


----Chinatown----
                venue  freq
0  Chinese Restaurant  0.06
1              Bakery  0.05
2        Cocktail Bar  0.04
3  Salon / Barbershop  0.03
4         Coffee Shop  0.03


----Civic Center----
               venue  freq
0  

##### Putting this in a pandas dataframe

In [73]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]



Creating a dataframe and displaying the top 10 venues in each neighborhood

In [74]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park                 Hotel   
1      Carnegie Hill           Coffee Shop                  Café   
2     Central Harlem                   Bar    Chinese Restaurant   
3            Chelsea           Art Gallery           Coffee Shop   
4          Chinatown    Chinese Restaurant                Bakery   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Gym         Boat or Ferry         Memorial Site   
1           Yoga Studio           Pizza Place                Bakery   
2   Fried Chicken Joint  Gym / Fitness Center    African Restaurant   
3    Italian Restaurant    Seafood Restaurant        Ice Cream Shop   
4          Cocktail Bar          Optical Shop   American Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Gourmet Shop            Food Court                 Plaza   
1                   Bar             Bookstore                   Gym   
2   American Restaurant     French Restaurant    Seafood Restaurant   
3             Juice Bar              Boutique             Bookstore   
4                   Spa           Coffee Shop    Salon / Barbershop   

  9th Most Common Venue 10th Most Common Venue  
0         Shopping Mall           Burger Joint  
1  Gym / Fitness Center    Japanese Restaurant  
2                   Gym               Beer Bar  
3        Clothing Store           Cupcake Shop  
4    Dim Sum Restaurant           Noodle House

### Cluster the neighborhoods in Manhattan using K-Means

In [75]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 1, 1, 2, 1, 1, 1, 0, 1, 1], dtype=int32)

In [76]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               1   
1  Manhattan           Chinatown  40.715618 -73.994279               1   
2  Manhattan  Washington Heights  40.851903 -73.936900               1   
3  Manhattan              Inwood  40.867684 -73.921210               0   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place                   Gym           Coffee Shop   
1    Chinese Restaurant                Bakery          Cocktail Bar   
2                  Café                Bakery         Grocery Store   
3    Mexican Restaurant                  Café                Bakery   
4           Pizza Place                  Café           Coffee Shop   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0           Yoga Studio         Deli / Bodega       Supplement Shop   
1          Optical Shop   American Restaurant                   Spa   
2    Chinese Restaurant           Pizza Place     Mobile Phone Shop   
3           Pizza Place                Lounge            Restaurant   
4    Mexican Restaurant         Deli / Bodega          Cocktail Bar   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Steakhouse    Seafood Restaurant           Pizza Place   
1           Coffee Shop    Salon / Barbershop    Dim Sum Restaurant   
2           Coffee Shop           Supermarket            Shoe Store   
3                  Park    Chinese Restaurant    Frozen Yogurt Shop   
4            Food Truck     Indian Restaurant           Yoga Studio   

  10th Most Common Venue  
0               Pharmacy  
1           Noodle House  
2                    Gym  
3    American Restaurant  
4       Sushi Restaurant

Lets now visualize the clusters

In [77]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

#### Examining the clusters

#### Cluster 1

In [78]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
3             Inwood    Mexican Restaurant                  Café   
4   Hamilton Heights           Pizza Place                  Café   
7        East Harlem    Mexican Restaurant                Bakery   
25  Manhattan Valley           Yoga Studio           Pizza Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
3                 Bakery           Pizza Place                Lounge   
4            Coffee Shop    Mexican Restaurant         Deli / Bodega   
7        Thai Restaurant         Deli / Bodega            Steakhouse   
25       Thai Restaurant                   Bar    Mexican Restaurant   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3                  Restaurant                  Park    Chinese Restaurant   
4                Cocktail Bar            Food Truck     Indian Restaurant   
7   Latin American Restaurant           Gas Station            Street Art   
25         Chinese Restaurant     Health Food Store   Peruvian Restaurant   

   9th Most Common Venue     10th Most Common Venue  
3     Frozen Yogurt Shop        American Restaurant  
4            Yoga Studio           Sushi Restaurant  
7                    Gym                   Beer Bar  
25                  Park  Latin American Restaurant

#### Cluster 2

In [79]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Marble Hill        Sandwich Place                   Gym   
1            Chinatown    Chinese Restaurant                Bakery   
2   Washington Heights                  Café                Bakery   
6       Central Harlem                   Bar    Chinese Restaurant   
8      Upper East Side    Italian Restaurant                Bakery   
9            Yorkville           Coffee Shop    Italian Restaurant   
10          Lenox Hill    Italian Restaurant           Coffee Shop   
11    Roosevelt Island                  Park        Baseball Field   
13      Lincoln Square                 Plaza                  Café   
14             Clinton               Theater  Gym / Fitness Center   
15             Midtown           Coffee Shop                 Hotel   
16         Murray Hill        Sandwich Place                   Bar   
19        East Village           Pizza Place           Coffee Shop   
20     Lower East Side                  Café          Cocktail Bar   
22        Little Italy    Chinese Restaurant    Italian Restaurant   
27            Gramercy    Italian Restaurant           Coffee Shop   
29  Financial District                 Hotel           Coffee Shop   
30       Carnegie Hill           Coffee Shop                  Café   
32        Civic Center                 Hotel           Coffee Shop   
36          Tudor City                  Café                  Park   
38            Flatiron  Gym / Fitness Center    Italian Restaurant   
39        Hudson Yards    Italian Restaurant   American Restaurant   

   3rd Most Common Venue          4th Most Common Venue 5th Most Common Venue  \
0            Coffee Shop                    Yoga Studio         Deli / Bodega   
1           Cocktail Bar                   Optical Shop   American Restaurant   
2          Grocery Store             Chinese Restaurant           Pizza Place   
6    Fried Chicken Joint           Gym / Fitness Center    African Restaurant   
8                Exhibit           Gym / Fitness Center                   Spa   
9                    Gym                            Bar      Sushi Restaurant   
10           Pizza Place                   Cocktail Bar      Sushi Restaurant   
11  Gym / Fitness Center              Kosher Restaurant      Greek Restaurant   
13    Italian Restaurant           Gym / Fitness Center               Theater   
14           Coffee Shop                      Wine Shop                   Gym   
15        Clothing Store                        Theater                   Spa   
16  Gym / Fitness Center                    Pizza Place     Indian Restaurant   
19                   Bar            Japanese Restaurant             Juice Bar   
20           Art Gallery                       Pharmacy    Chinese Restaurant   
22                Bakery                Thai Restaurant                 Hotel   
27            Playground                    Pizza Place                   Bar   
29                  Café           Gym / Fitness Center           Pizza Place   
30           Yoga Studio                    Pizza Place                Bakery   
32     French Restaurant                            Spa           Yoga Studio   
36      Greek Restaurant             Mexican Restaurant         Deli / Bodega   
38                   Gym  Vegetarian / Vegan Restaurant                  Café   
39  Gym / Fitness Center                           Café                 Hotel   

       6th Most Common Venue 7th Most Common Venue      8th Most Common Venue  \
0            Supplement Shop            Steakhouse         Seafood Restaurant   
1                        Spa           Coffee Shop         Salon / Barbershop   
2          Mobile Phone Shop           Coffee Shop                Supermarket   
6        American Restaurant     French Restaurant         Seafood Restaurant   
8        American Restaurant             Juice Bar                Pizza Place   
9              Deli / Bodega             Wine Sho

#### Cluster 3

In [80]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
5        Manhattanville           Coffee Shop    Seafood Restaurant   
12      Upper West Side    Italian Restaurant           Coffee Shop   
17              Chelsea           Art Gallery           Coffee Shop   
18    Greenwich Village    Italian Restaurant           Coffee Shop   
21              Tribeca    Italian Restaurant                  Park   
23                 Soho    Italian Restaurant           Coffee Shop   
24         West Village    Italian Restaurant              Wine Bar   
26  Morningside Heights                  Park             Bookstore   
28    Battery Park City                  Park                 Hotel   
31                 Noho    Italian Restaurant           Coffee Shop   
34         Sutton Place    Italian Restaurant           Coffee Shop   
35           Turtle Bay    Italian Restaurant           Coffee Shop   

       3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
5         Italian Restaurant                  Park              Deli / Bodega   
12                  Wine Bar                Bakery  Middle Eastern Restaurant   
17        Italian Restaurant    Seafood Restaurant             Ice Cream Shop   
18                      Café      Sushi Restaurant                   Wine Bar   
21                  Wine Bar                  Café                        Spa   
23  Mediterranean Restaurant          Dessert Shop                        Gym   
24   New American Restaurant                  Park                Coffee Shop   
26       American Restaurant           Coffee Shop               Burger Joint   
28                       Gym         Boat or Ferry              Memorial Site   
31            Sandwich Place         Grocery Store        Japanese Restaurant   
34      Gym / Fitness Center                  Park                 Bagel Shop   
35          Sushi Restaurant                  Park              Deli / Bodega   

       6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
5         Mexican Restaurant           Supermarket          Liquor Store   
12  Mediterranean Restaurant            Bagel Shop     Indian Restaurant   
17                 Juice Bar              Boutique             Bookstore   
18              Dessert Shop    Chinese Restaurant           Comedy Club   
21       American Restaurant      Greek Restaurant            Poke Place   
23         French Restaurant                  Café           Art Gallery   
24       American Restaurant    Seafood Restaurant     Food & Drink Shop   
26             Deli / Bodega          Tennis Court              Pharmacy   
28              Gourmet Shop            Food Court                 Plaza   
31                  Wine Bar           Pizza Place                   Bar   
34                     Hotel            Smoke Shop              Beer Bar   
35                      Café                 Hotel              Wine Bar   

   9th Most Common Venue 10th Most Common Venue  
5                 Lounge             Bike Trail  
12        Ice Cream Shop                    Bar  
17        Clothing Store           Cupcake Shop  
18                   Gym           Gourmet Shop  
21                 Hotel            Art Gallery  
23                   Spa          Women's Store  
24               Theater                 Bakery  
26           Supermarket                   Café  
28         Shopping Mall           Burger Joint  
31    Seafood Restaurant              Wine Shop  
34           Beer Garden          Grocery Store  
35     French Restaurant     Seafood Restaurant

#### Cluster 4

In [81]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37  Stuyvesant Town         Boat or Ferry                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
37  Gym / Fitness Center        Baseball Field       Harbor / Marina   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
37          Cocktail Bar           Coffee Shop              Heliport   

   9th Most Common Venue 10th Most Common Venue  
37     German Restaurant         Farmers Market

#### Cluster 5

In [82]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
33  Midtown South     Korean Restaurant                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
33   Japanese Restaurant             Hotel Bar  Gym / Fitness Center   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
33          Burger Joint                  Café           Salad Place   

   9th Most Common Venue   10th Most Common Venue  
33            Donut Shop  New American Restaurant

#### Completion of Analysis for Manhattan

We have now completed the analysis and clustering for Manhattan and this would now help Mr.John take an informed decision if he wishes to relocate to any of the neighborhoods in Manhattan.

However our analysis is still not complete. Remember there are other Boroughs in New York and we have not done any analysis on those. We will now proceed to do similar analysis for each of the other Boroughs so that Mr.John has all of the required information to make an informed Decision.

### Let us now proceed onto Staten Island do similar analysis and clustering of those neighborhoods

Lets now create a new Dataframe which has only Staten Island neighborhoods

In [83]:
SI_data = neighborhoods[neighborhoods['Borough'] == 'Staten Island'].reset_index(drop=True)
SI_data.head(500)

Borough       Neighborhood   Latitude  Longitude
0   Staten Island         St. George  40.644982 -74.079353
1   Staten Island       New Brighton  40.640615 -74.087017
2   Staten Island          Stapleton  40.626928 -74.077902
3   Staten Island           Rosebank  40.615305 -74.069805
4   Staten Island      West Brighton  40.631879 -74.107182
5   Staten Island        Grymes Hill  40.624185 -74.087248
6   Staten Island          Todt Hill  40.597069 -74.111329
7   Staten Island        South Beach  40.580247 -74.079553
8   Staten Island      Port Richmond  40.633669 -74.129434
9   Staten Island   Mariner's Harbor  40.632546 -74.150085
10  Staten Island         Port Ivory  40.639683 -74.174645
11  Staten Island  Castleton Corners  40.613336 -74.119181
12  Staten Island    New Springville  40.594252 -74.164960
13  Staten Island             Travis  40.586314 -74.190737
14  Staten Island           New Dorp  40.572572 -74.116479
15  Staten Island            Oakwood  40.558462 -74.121566
16  Staten Island        Great Kills  40.549480 -74.149324
17  Staten Island        Eltingville  40.542231 -74.164331
18  Staten Island           Annadale  40.538114 -74.178549
19  Staten Island            Woodrow  40.541968 -74.205246
20  Staten Island        Tottenville  40.505334 -74.246569
21  Staten Island      Tompkinsville  40.637316 -74.080554
22  Staten Island        Silver Lake  40.619193 -74.096290
23  Staten Island          Sunnyside  40.612760 -74.097126
24  Staten Island          Park Hill  40.609190 -74.080157
25  Staten Island        Westerleigh  40.621090 -74.133041
26  Staten Island       Graniteville  40.620172 -74.153152
27  Staten Island          Arlington  40.635325 -74.165104
28  Staten Island           Arrochar  40.596313 -74.067124
29  Staten Island           Grasmere  40.598268 -74.076674
30  Staten Island           Old Town  40.596329 -74.087511
31  Staten Island       Dongan Hills  40.588673 -74.096399
32  Staten Island      Midland Beach  40.573527 -74.093483
33  Staten Island         Grant City  40.576216 -74.105856
34  Staten Island     New Dorp Beach  40.564255 -74.104327
35  Staten Island        Bay Terrace  40.553988 -74.139166
36  Staten Island           Huguenot  40.531912 -74.191741
37  Staten Island    Pleasant Plains  40.524699 -74.219831
38  Staten Island       Butler Manor  40.506082 -74.229504
39  Staten Island         Charleston  40.530531 -74.232158
40  Staten Island          Rossville  40.549404 -74.215729
41  Staten Island      Arden Heights  40.549286 -74.185887
42  Staten Island         Greenridge  40.555295 -74.170794
43  Staten Island  Heartland Village  40.589139 -74.159022
44  Staten Island            Chelsea  40.594726 -74.189560
45  Staten Island         Bloomfield  40.605779 -74.187256
46  Staten Island         Bulls Head  40.609592 -74.159409
47  Staten Island      Richmond Town  40.569606 -74.134057
48  Staten Island        Shore Acres  40.609719 -74.066678
49  Staten Island            Clifton  40.619178 -74.072642
50  Staten Island            Concord  40.604473 -74.084024
51  Staten Island       Emerson Hill  40.606794 -74.097762
52  Staten Island      Randall Manor  40.635630 -74.098051
53  Staten Island       Howland Hook  40.638433 -74.186223
54  Staten Island           Elm Park  40.630147 -74.141817
55  Staten Island      Manor Heights  40.601810 -74.120594
56  Staten Island        Willowbrook  40.603707 -74.132084
57  Staten Island       Sandy Ground  40.541140 -74.217766
58  Staten Island        Egbertville  40.579119 -74.127272
59  Staten Island       Prince's Bay  40.526264 -74.201526
60  Staten Island    Lighthouse Hill  40.576506 -74.137927
61  Staten Island    Richmond Valley  40.519541 -74.229571
62  Staten Island          Fox Hills  40.617311 -74.081740

Lets also get the Latitude and Longitude co-ordinates for Staten Island using the geopy library

In [84]:
address = 'Staten Island, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
SIlatitude = location.latitude
SIlongitude = location.longitude
print('The geograpical coordinate of Staten Island are {}, {}.'.format(SIlatitude, SIlongitude))

The geograpical coordinate of Staten Island are 40.5834557, -74.1496048.


A picture says a thousand words, so lets create a map using Folium and superimpose the Staten Island data alone

In [85]:
map_SI = folium.Map(location=[SIlatitude, SIlongitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(SI_data['Latitude'], SI_data['Longitude'], SI_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_SI)  
    
map_SI

Lets reuse the function we created for Manhattan but this time around we are going to get the Top 100 venues and within the radius of 500 meters of each neighborhood in Staten Island

In [23]:
# type your answer here
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

SI_venues = getNearbyVenues(names=SI_data['Neighborhood'],
                                   latitudes=SI_data['Latitude'],
                                   longitudes=SI_data['Longitude']
                                  )

St. George
New Brighton
Stapleton
Rosebank
West Brighton
Grymes Hill
Todt Hill
South Beach
Port Richmond
Mariner's Harbor
Port Ivory
Castleton Corners
New Springville
Travis
New Dorp
Oakwood
Great Kills
Eltingville
Annadale
Woodrow
Tottenville
Tompkinsville
Silver Lake
Sunnyside
Park Hill
Westerleigh
Graniteville
Arlington
Arrochar
Grasmere
Old Town
Dongan Hills
Midland Beach
Grant City
New Dorp Beach
Bay Terrace
Huguenot
Pleasant Plains
Butler Manor
Charleston
Rossville
Arden Heights
Greenridge
Heartland Village
Chelsea
Bloomfield
Bulls Head
Richmond Town
Shore Acres
Clifton
Concord
Emerson Hill
Randall Manor
Howland Hook
Elm Park
Manor Heights
Willowbrook
Sandy Ground
Egbertville
Prince's Bay
Lighthouse Hill
Richmond Valley
Fox Hills


#### Lets check the size of this dataframe

In [24]:
print(SI_venues.shape)
SI_venues.head()

(825, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   St. George              40.644982              -74.079353   
1   St. George              40.644982              -74.079353   
2   St. George              40.644982              -74.079353   
3   St. George              40.644982              -74.079353   
4   St. George              40.644982              -74.079353   

                                 Venue  Venue Latitude  Venue Longitude  \
0                         A&S Pizzeria       40.643940       -74.077626   
1                                 Beso       40.643306       -74.076508   
2        Richmond County Bank Ballpark       40.645056       -74.076864   
3  Staten Island September 11 Memorial       40.646767       -74.076510   
4                   Nike Factory Store       40.645753       -74.077702   

        Venue Category  
0          Pizza Place  
1     Tapas Restaurant  
2     Baseball Stadium  
3  Monument / Landmark  
4  Sporting Goods Shop

Grouping the Venues by Neighborhood

In [25]:
SI_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                              
Annadale                              12                      12     12   
Arden Heights                          6                       6      6   
Arlington                              6                       6      6   
Arrochar                              22                      22     22   
Bay Terrace                            9                       9      9   
Bloomfield                             5                       5      5   
Bulls Head                            44                      44     44   
Butler Manor                           5                       5      5   
Castleton Corners                     15                      15     15   
Charleston                            29                      29     29   
Chelsea                                6                       6      6   
Clifton                               19                      19     19   
Concord                                6                       6      6   
Dongan Hills                          23                      23     23   
Egbertville                            5                       5      5   
Elm Park                              11                      11     11   
Eltingville                           40                      40     40   
Fox Hills                              4                       4      4   
Graniteville                           3                       3      3   
Grant City                            22                      22     22   
Grasmere                              21                      21     21   
Great Kills                           20                      20     20   
Greenridge                             7                       7      7   
Grymes Hill                            3                       3      3   
Heartland Village                     11                      11     11   
Huguenot                              10                      10     10   
Lighthouse Hill                        5                       5      5   
Manor Heights                         12                      12     12   
Mariner's Harbor                       7                       7      7   
Midland Beach                         12                      12     12   
New Brighton                          11                      11     11   
New Dorp                              25                      25     25   
New Dorp Beach                        12                      12     12   
New Springville                       26                      26     26   
Oakwood                                4                       4      4   
Old Town                              17                      17     17   
Park Hill                              6                       6      6   
Pleasant Plains                       20                      20     20   
Port Richmond                          5                       5      5   
Prince's Bay                           9                       9      9   
Randall Manor                          5                       5      5   
Richmond Town                          5                       5      5   
Richmond Valley                       10                      10     10   
Rosebank                              27                      27     27   
Rossville                             15                      15     15   
Sandy Ground                           5                       5      5   
Shore Acres                           26                      26     26   
Silver Lake                            4                       4      4   
South Beach                            7                       7      7   
St. George                            32                      32     32   
Stapleton                             30                      30     30   
Sunnyside                              6    

In [26]:
print('There are {} uniques categories.'.format(len(SI_venues['Venue Category'].unique())))

There are 175 uniques categories.


#### Lets analyze each neighborhood in Staten Island

In [27]:
# one hot encoding
SI_onehot = pd.get_dummies(SI_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
SI_onehot['Neighborhood'] = SI_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [SI_onehot.columns[-1]] + list(SI_onehot.columns[:-1])
SI_onehot = SI_onehot[fixed_columns]

SI_onehot.head()

Neighborhood  Accessories Store  American Restaurant  Arcade  Art Museum  \
0   St. George                  0                    0       0           0   
1   St. George                  0                    0       0           0   
2   St. George                  0                    0       0           0   
3   St. George                  0                    0       0           0   
4   St. George                  0                    0       0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                    0                 0                   0          0   
1                    0                 0                   0          0   
2                    0                 0                   0          0   
3                    0                 0                   0          0   
4                    0                 0                   0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 1   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Beach  Beer Bar  Big Box Store  Board Shop  \
0                 0      0         0              0           0   
1                 0      0         0              0           0   
2                 0      0         0              0           0   
3                 0      0         0              0           0   
4                 0      0         0              0           0   

   Boat or Ferry  Bookstore  Bowling Alley  Breakfast Spot  Brewery  \
0              0          0              0               0        0   
1              0          0              0               0        0   
2              0          0              0               0        0   
3              0          0              0               0        0   
4              0          0              0               0        0   

   Bridal Shop  Burger Joint  Bus Stop  Café  Cajun / Creole Restaurant  \
0            0             0         0     0                          0   
1            0             0         0     0                          0   
2            0             0         0     0                          0   
3            0             0         0     0                          0   
4            0             0         0     0                          0   

   Campground  Caribbean Restaurant  Check Cashing Service  \
0           0                     0                      0   
1           0                     0                      0   
2           0                     0                      0   
3           0                     0                      0   
4           0                     0                      0   

   Chinese Restaurant  Clothing Store  Coffee Shop  Comedy Club  Concert Hall  \
0                   0               0            0            0             0   
1                   0               0            0            0             0   
2                   0               0            0            0             0   
3                   0               0            0            0             0   
4                   0               0            0            0             0   

   Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0                           0                  0               0   
1                           0                  0               0   
2                           0                  0               0   
3                           0                  0               0   
4                           0                  0               0   

   Cycle Studio  Dance Studio  Deli / Bodega  Department Store  Dessert Shop  \
0             0             0  

In [28]:
SI_onehot.shape

(825, 176)

#### Lets group the rows by Neighborhood and by taking the mean of the frequency of occurance of each category

In [29]:
SI_grouped = SI_onehot.groupby('Neighborhood').mean().reset_index()
SI_grouped

Neighborhood  Accessories Store  American Restaurant  Arcade  \
0            Annadale           0.000000             0.083333    0.00   
1       Arden Heights           0.000000             0.000000    0.00   
2           Arlington           0.000000             0.000000    0.00   
3            Arrochar           0.000000             0.000000    0.00   
4         Bay Terrace           0.000000             0.000000    0.00   
5          Bloomfield           0.000000             0.000000    0.00   
6          Bulls Head           0.000000             0.022727    0.00   
7        Butler Manor           0.000000             0.000000    0.00   
8   Castleton Corners           0.000000             0.000000    0.00   
9          Charleston           0.000000             0.034483    0.00   
10            Chelsea           0.000000             0.000000    0.00   
11            Clifton           0.000000             0.052632    0.00   
12            Concord           0.000000             0.000000    0.00   
13       Dongan Hills           0.000000             0.000000    0.00   
14        Egbertville           0.000000             0.000000    0.00   
15           Elm Park           0.000000             0.090909    0.00   
16        Eltingville           0.000000             0.000000    0.00   
17          Fox Hills           0.000000             0.000000    0.00   
18       Graniteville           0.000000             0.000000    0.00   
19         Grant City           0.000000             0.000000    0.00   
20           Grasmere           0.000000             0.000000    0.00   
21        Great Kills           0.000000             0.000000    0.00   
22         Greenridge           0.000000             0.000000    0.00   
23        Grymes Hill           0.000000             0.000000    0.00   
24  Heartland Village           0.090909             0.000000    0.00   
25           Huguenot           0.000000             0.000000    0.00   
26    Lighthouse Hill           0.000000             0.000000    0.00   
27      Manor Heights           0.000000             0.083333    0.00   
28   Mariner's Harbor           0.000000             0.000000    0.00   
29      Midland Beach           0.000000             0.000000    0.00   
30       New Brighton           0.000000             0.000000    0.00   
31           New Dorp           0.000000             0.000000    0.00   
32     New Dorp Beach           0.000000             0.000000    0.00   
33    New Springville           0.038462             0.000000    0.00   
34            Oakwood           0.000000             0.000000    0.00   
35           Old Town           0.000000             0.058824    0.00   
36          Park Hill           0.000000             0.000000    0.00   
37    Pleasant Plains           0.000000             0.000000    0.00   
38      Port Richmond           0.000000             0.000000    0.00   
39       Prince's Bay           0.000000             0.000000    0.00   
40      Randall Manor           0.000000             0.000000    0.00   
41      Richmond Town           0.000000             0.000000    0.00   
42    Richmond Valley           0.000000             0.000000    0.00   
43           Rosebank           0.000000             0.000000    0.00   
44          Rossville           0.000000             0.066667    0.00   
45       Sandy Ground           0.000000             0.000000    0.00   
46        Shore Acres           0.000000             0.000000    0.00   
47        Silver Lake           0.000000             0.250000    0.00   
48        South Beach           0.000000             0.000000    0.00   
49         St. George           0.000000             0.031250    0.00   
50          Stapleton           0.000000             0.000000    0.00   
51          Sunnyside           0.000000             0.166667    0.00   
52          Todt Hill           0.000000             0.000000    0.00   
53      Tompkinsville           0.000000             0.000000    0.

In [30]:
SI_grouped.shape

(60, 176)

#####  Printing each neighborhood along with the top 5 most common venues

In [31]:
num_top_venues = 5

for hood in SI_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = SI_grouped[SI_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Annadale----
                 venue  freq
0          Pizza Place  0.17
1                Diner  0.08
2             Pharmacy  0.08
3  American Restaurant  0.08
4         Liquor Store  0.08


----Arden Heights----
           venue  freq
0    Coffee Shop  0.17
1       Bus Stop  0.17
2  Deli / Bodega  0.17
3       Pharmacy  0.17
4   Home Service  0.17


----Arlington----
           venue  freq
0       Bus Stop  0.33
1    Coffee Shop  0.17
2   Intersection  0.17
3  Deli / Bodega  0.17
4  Grocery Store  0.17


----Arrochar----
                venue  freq
0  Italian Restaurant  0.09
1          Bagel Shop  0.09
2       Deli / Bodega  0.09
3            Bus Stop  0.09
4          Taco Place  0.05


----Bay Terrace----
                venue  freq
0         Supermarket  0.22
1        Home Service  0.11
2          Donut Shop  0.11
3  Salon / Barbershop  0.11
4               Plaza  0.11


----Bloomfield----
               venue  freq
0         Theme Park   0.2
1     Discount Store   0.2
2  Recreat

##### Putting this in a pandas dataframe

In [32]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]



Creating a dataframe and displaying the top 10 venues in each neighborhood

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = SI_grouped['Neighborhood']

for ind in np.arange(SI_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(SI_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Annadale           Pizza Place          Dance Studio   
1  Arden Heights           Coffee Shop         Deli / Bodega   
2      Arlington              Bus Stop         Deli / Bodega   
3       Arrochar    Italian Restaurant         Deli / Bodega   
4    Bay Terrace           Supermarket    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Bakery                 Diner            Restaurant   
1              Bus Stop          Home Service           Pizza Place   
2          Intersection         Grocery Store           Coffee Shop   
3            Bagel Shop              Bus Stop        Sandwich Place   
4    Salon / Barbershop      Sushi Restaurant        Shipping Store   

  6th Most Common Venue 7th Most Common Venue     8th Most Common Venue  \
0              Pharmacy            Sports Bar              Liquor Store   
1              Pharmacy    Falafel Restaurant         Food & Drink Shop   
2        Farmers Market            Food Truck         Food & Drink Shop   
3          Liquor Store            Taco Place  Mediterranean Restaurant   
4            Donut Shop          Home Service                     Plaza   

  9th Most Common Venue 10th Most Common Venue  
0                   Pub          Train Station  
1                  Food            Flower Shop  
2                  Food            Flower Shop  
3                 Hotel  Outdoors & Recreation  
4                 Diner     Falafel Restaurant

### Cluster the neighborhoods in Staten Island using K-Means

In [34]:
# set number of clusters
kclusters = 5

SI_grouped_clustering = SI_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(SI_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 1, 0, 0, 1, 0, 0, 0, 0], dtype=int32)

In [35]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

SI_merged = SI_data

SI_merged = SI_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

SI_merged.head() # check the last columns!

Borough   Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Staten Island     St. George  40.644982 -74.079353             0.0   
1  Staten Island   New Brighton  40.640615 -74.087017             1.0   
2  Staten Island      Stapleton  40.626928 -74.077902             0.0   
3  Staten Island       Rosebank  40.615305 -74.069805             0.0   
4  Staten Island  West Brighton  40.631879 -74.107182             0.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Clothing Store   Sporting Goods Shop                   Bar   
1              Bus Stop                  Park         Deli / Bodega   
2        Discount Store                  Bank        Sandwich Place   
3    Italian Restaurant              Pharmacy         Grocery Store   
4                   Bar           Coffee Shop           Music Store   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0    Italian Restaurant         Deli / Bodega           Pizza Place   
1         Bowling Alley        Discount Store            Playground   
2           Pizza Place    Mexican Restaurant                  Park   
3                Museum      Storage Facility        Breakfast Spot   
4              Pharmacy        Breakfast Spot                  Bank   

  7th Most Common Venue                     8th Most Common Venue  \
0                 Plaza                               Outlet Mall   
1            Food Truck                         Food & Drink Shop   
2            Donut Shop  Residential Building (Apartment / Condo)   
3           Pizza Place                                      Café   
4    Italian Restaurant                                 Gift Shop   

       9th Most Common Venue   10th Most Common Venue  
0                 Donut Shop              Coffee Shop  
1                       Food              Flower Shop  
2                 Restaurant  New American Restaurant  
3  Cajun / Creole Restaurant      Filipino Restaurant  
4          German Restaurant                 Bus Stop

#### Examining the clusters

#### Cluster 1

In [36]:
SI_merged.loc[SI_merged['Cluster Labels'] == 0, SI_merged.columns[[1] + list(range(5, SI_merged.shape[1]))]]

Neighborhood       1st Most Common Venue    2nd Most Common Venue  \
0          St. George              Clothing Store      Sporting Goods Shop   
2           Stapleton              Discount Store                     Bank   
3            Rosebank          Italian Restaurant                 Pharmacy   
4       West Brighton                         Bar              Coffee Shop   
8       Port Richmond         Rental Car Location       Mexican Restaurant   
11  Castleton Corners                 Pizza Place                     Bank   
12    New Springville                 Pizza Place  Health & Beauty Service   
13             Travis                       Hotel            Deli / Bodega   
14           New Dorp          Italian Restaurant              Pizza Place   
16        Great Kills          Italian Restaurant              Pizza Place   
17        Eltingville                 Pizza Place         Sushi Restaurant   
18           Annadale                 Pizza Place             Dance Studio   
19            Woodrow                    Pharmacy       Italian Restaurant   
21      Tompkinsville                     Brewery                Gastropub   
22        Silver Lake               Indie Theater      American Restaurant   
23          Sunnyside         American Restaurant                     Café   
25        Westerleigh                      Arcade                 Dive Bar   
26       Graniteville               Boat or Ferry           Sandwich Place   
28           Arrochar          Italian Restaurant            Deli / Bodega   
30           Old Town          Italian Restaurant                   Bakery   
31       Dongan Hills                 Pizza Place       Italian Restaurant   
32      Midland Beach                       Beach            Deli / Bodega   
33         Grant City        Fast Food Restaurant              Pizza Place   
35        Bay Terrace                 Supermarket       Italian Restaurant   
36           Huguenot                        Bank         Asian Restaurant   
37    Pleasant Plains                 Pizza Place            Deli / Bodega   
38       Butler Manor              Baseball Field                     Pool   
39         Charleston              Cosmetics Shop            Big Box Store   
40          Rossville                 Pizza Place               Bagel Shop   
41      Arden Heights                 Coffee Shop            Deli / Bodega   
42         Greenridge  Construction & Landscaping                    Diner   
43  Heartland Village                 Coffee Shop        Accessories Store   
44            Chelsea              Ice Cream Shop           Sandwich Place   
46         Bulls Head                    Bus Stop              Pizza Place   
49            Clifton               Grocery Store            Train Station   
50            Concord               Deli / Bodega                     Park   
54           Elm Park                    Bus Stop       Italian Restaurant   
55      Manor Heights               Deli / Bodega             Liquor Store   
59       Prince's Bay                 Pizza Place       Italian Restaurant   
61    Richmond Valley                        Bank       Mexican Restaurant   

     3rd Most Common Venue       4th Most Common Venue  \
0                      Bar          Italian Restaurant   
2           Sandwich Place                 Pizza Place   
3            Grocery Store                      Museum   
4              Music Store                    Pharmacy   
8            Deli / Bodega  Construction & Landscaping   
11          Ice Cream Shop               Go Kart Track   
12      Chinese Restaurant                 Coffee Shop   
13          Baseball Field                 Comedy Club   
14   Vietnamese Restaurant        Gym / Fitness Center   
16                     Bar          Falafel Restaurant   
17    Fast Food Restaurant                Liquor Store   
18                  Bakery                       Diner   
19       Martial Arts Dojo                 Pizza Place  

#### Cluster 2

In [37]:
SI_merged.loc[SI_merged['Cluster Labels'] == 1, SI_merged.columns[[1] + list(range(5, SI_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
1    New Brighton              Bus Stop                  Park   
7     South Beach                  Pier                 Beach   
15        Oakwood              Bus Stop                Lawyer   
24      Park Hill              Bus Stop           Coffee Shop   
27      Arlington              Bus Stop         Deli / Bodega   
29       Grasmere              Bus Stop                  Bank   
45     Bloomfield     Recreation Center            Theme Park   
52  Randall Manor              Bus Stop                  Park   
57   Sandy Ground          Intersection              Bus Stop   

   3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
1          Deli / Bodega         Bowling Alley              Discount Store   
7          Deli / Bodega              Bus Stop          Athletics & Sports   
15            Playground                   Bar                 Yoga Studio   
24                 Hotel    Athletics & Sports        Gym / Fitness Center   
27          Intersection         Grocery Store                 Coffee Shop   
29    Italian Restaurant   Japanese Restaurant                   Juice Bar   
45              Bus Stop        Discount Store                        Park   
52            Playground           Yoga Studio              Farmers Market   
57          Home Service                Market  Construction & Landscaping   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1             Playground            Food Truck     Food & Drink Shop   
7            Yoga Studio  Fast Food Restaurant     French Restaurant   
15    Falafel Restaurant            Food Truck     Food & Drink Shop   
24    Falafel Restaurant            Food Truck     Food & Drink Shop   
27        Farmers Market            Food Truck     Food & Drink Shop   
29         Grocery Store            Nail Salon              Pharmacy   
45     Food & Drink Shop                  Food           Flower Shop   
52            Food Truck     Food & Drink Shop                  Food   
57    Falafel Restaurant            Food Truck     Food & Drink Shop   

   9th Most Common Venue 10th Most Common Venue  
1                   Food            Flower Shop  
7             Food Truck      Food & Drink Shop  
15                  Food            Flower Shop  
24                  Food            Flower Shop  
27                  Food            Flower Shop  
29        Ice Cream Shop             Restaurant  
45   Filipino Restaurant   Fast Food Restaurant  
52           Flower Shop    Filipino Restaurant  
57                  Food            Flower Shop

#### Cluster 3

In [38]:
SI_merged.loc[SI_merged['Cluster Labels'] == 2, SI_merged.columns[[1] + list(range(5, SI_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
6    Todt Hill                  Park           Yoga Studio   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6          Intersection     French Restaurant            Food Truck   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6     Food & Drink Shop                  Food           Flower Shop   

  9th Most Common Venue 10th Most Common Venue  
6   Filipino Restaurant   Fast Food Restaurant

#### Cluster 4

In [39]:
SI_merged.loc[SI_merged['Cluster Labels'] == 3, SI_merged.columns[[1] + list(range(5, SI_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
5   Grymes Hill              Bus Stop               Dog Run   
56  Willowbrook              Bus Stop          Intersection   
62    Fox Hills              Bus Stop        Sandwich Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
5            Yoga Studio        Farmers Market     French Restaurant   
56         Deli / Bodega           Pizza Place    Falafel Restaurant   
62           Yoga Studio    Falafel Restaurant            Food Truck   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
5             Food Truck     Food & Drink Shop                  Food   
56            Food Truck     Food & Drink Shop                  Food   
62     Food & Drink Shop                  Food           Flower Shop   

   9th Most Common Venue 10th Most Common Venue  
5            Flower Shop    Filipino Restaurant  
56           Flower Shop    Filipino Restaurant  
62   Filipino Restaurant   Fast Food Restaurant

#### Cluster 5

In [40]:
SI_merged.loc[SI_merged['Cluster Labels'] == 4, SI_merged.columns[[1] + list(range(5, SI_merged.shape[1]))]]

Neighborhood 1st Most Common Venue   2nd Most Common Venue  \
9   Mariner's Harbor    Italian Restaurant           Deli / Bodega   
20       Tottenville    Italian Restaurant  Thrift / Vintage Store   
34    New Dorp Beach    Italian Restaurant           Deli / Bodega   
47     Richmond Town    Italian Restaurant                    Café   
48       Shore Acres         Deli / Bodega      Italian Restaurant   
58       Egbertville    Italian Restaurant          Cosmetics Shop   
60   Lighthouse Hill    Italian Restaurant              Art Museum   

         3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
9                     Bus Stop     Other Repair Shop  Furniture / Home Store   
20                      Lawyer    Mexican Restaurant          Cosmetics Shop   
34                       Diner            Restaurant                    Food   
47                         Spa            Bagel Shop          History Museum   
48                    Bus Stop                   Bar            Intersection   
58  Construction & Landscaping            Bagel Shop          Clothing Store   
60                        Café                 Trail                     Spa   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
9         Farmers Market            Food Truck     Food & Drink Shop   
20              Bus Stop         Deli / Bodega    Athletics & Sports   
34            Sports Bar        Scenic Lookout                 Beach   
47        Farmers Market            Food Truck     Food & Drink Shop   
48           Supermarket            Bagel Shop        Baseball Field   
58        Farmers Market     French Restaurant            Food Truck   
60    Falafel Restaurant            Food Truck     Food & Drink Shop   

   9th Most Common Venue 10th Most Common Venue  
9                   Food            Flower Shop  
20     German Restaurant            Gas Station  
34          Skating Rink           Dessert Shop  
47                  Food            Flower Shop  
48    Chinese Restaurant           Concert Hall  
58     Food & Drink Shop                   Food  
60                  Food            Flower Shop

#### Completion of Analysis for Staten Island

We have now completed the analysis and clustering for Staten Island and this would now help Mr.John take an informed decision if he wishes to relocate to any of the neighborhoods in Staten Island.

However our analysis is still not complete. Remember there are other Boroughs in New York and we have not done any analysis on those. We will now proceed to do similar analysis for each of the other Boroughs so that Mr.John has all of the required information to make an informed Decision.

### Let us now proceed onto Brooklyn do similar analysis and clustering of those neighborhoods

Lets now create a new Dataframe which has only Brooklyn neighborhoods

In [86]:
br_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
br_data.head(500)

Borough               Neighborhood   Latitude  Longitude
0   Brooklyn                  Bay Ridge  40.625801 -74.030621
1   Brooklyn                Bensonhurst  40.611009 -73.995180
2   Brooklyn                Sunset Park  40.645103 -74.010316
3   Brooklyn                 Greenpoint  40.730201 -73.954241
4   Brooklyn                  Gravesend  40.595260 -73.973471
5   Brooklyn             Brighton Beach  40.576825 -73.965094
6   Brooklyn             Sheepshead Bay  40.586890 -73.943186
7   Brooklyn          Manhattan Terrace  40.614433 -73.957438
8   Brooklyn                   Flatbush  40.636326 -73.958401
9   Brooklyn              Crown Heights  40.670829 -73.943291
10  Brooklyn              East Flatbush  40.641718 -73.936103
11  Brooklyn                 Kensington  40.642382 -73.980421
12  Brooklyn            Windsor Terrace  40.656946 -73.980073
13  Brooklyn           Prospect Heights  40.676822 -73.964859
14  Brooklyn                Brownsville  40.663950 -73.910235
15  Brooklyn               Williamsburg  40.707144 -73.958115
16  Brooklyn                   Bushwick  40.698116 -73.925258
17  Brooklyn         Bedford Stuyvesant  40.687232 -73.941785
18  Brooklyn           Brooklyn Heights  40.695864 -73.993782
19  Brooklyn                Cobble Hill  40.687920 -73.998561
20  Brooklyn            Carroll Gardens  40.680540 -73.994654
21  Brooklyn                   Red Hook  40.676253 -74.012759
22  Brooklyn                    Gowanus  40.673931 -73.994441
23  Brooklyn                Fort Greene  40.688527 -73.972906
24  Brooklyn                 Park Slope  40.672321 -73.977050
25  Brooklyn              Cypress Hills  40.682391 -73.876616
26  Brooklyn              East New York  40.669926 -73.880699
27  Brooklyn              Starrett City  40.647589 -73.879370
28  Brooklyn                   Canarsie  40.635564 -73.902093
29  Brooklyn                  Flatlands  40.630446 -73.929113
30  Brooklyn                Mill Island  40.606336 -73.908186
31  Brooklyn            Manhattan Beach  40.577914 -73.943537
32  Brooklyn               Coney Island  40.574293 -73.988683
33  Brooklyn                 Bath Beach  40.599519 -73.998752
34  Brooklyn               Borough Park  40.633131 -73.990498
35  Brooklyn              Dyker Heights  40.619219 -74.019314
36  Brooklyn            Gerritsen Beach  40.590848 -73.930102
37  Brooklyn                Marine Park  40.609748 -73.931344
38  Brooklyn               Clinton Hill  40.693229 -73.967843
39  Brooklyn                   Sea Gate  40.576375 -74.007873
40  Brooklyn                   Downtown  40.690844 -73.983463
41  Brooklyn                Boerum Hill  40.685683 -73.983748
42  Brooklyn  Prospect Lefferts Gardens  40.658420 -73.954899
43  Brooklyn                 Ocean Hill  40.678403 -73.913068
44  Brooklyn                  City Line  40.678570 -73.867976
45  Brooklyn               Bergen Beach  40.615150 -73.898556
46  Brooklyn                    Midwood  40.625596 -73.957595
47  Brooklyn        Prospect Park South  40.647009 -73.962613
48  Brooklyn                 Georgetown  40.623845 -73.916075
49  Brooklyn          East Williamsburg  40.708492 -73.938858
50  Brooklyn                 North Side  40.714823 -73.958809
51  Brooklyn                 South Side  40.710861 -73.958001
52  Brooklyn              Ocean Parkway  40.613060 -73.968367
53  Brooklyn              Fort Hamilton  40.614768 -74.031979
54  Brooklyn                Ditmas Park  40.643675 -73.961013
55  Brooklyn                    Wingate  40.660947 -73.937187
56  Brooklyn                      Rugby  40.655572 -73.926882
57  Brooklyn             Remsen Village  40.652117 -73.916653
58  Brooklyn                   New Lots  40.662744 -73.885118
59  Brooklyn            Paerdegat Basin  40.631318 -73.902335
60  Brooklyn                 Mill Basin  40.615974 -73.915154
61  Brooklyn               Fulton Ferry  40.703281 -73.995508
62  Brooklyn               Vinegar Hill  40.703321 -73.981116
63  Brooklyn                 Weeksvil

Lets also get the Latitude and Longitude co-ordinates for Brooklyn using the geopy library

In [87]:
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
brlatitude = location.latitude
brlongitude = location.longitude
print('The geograpical coordinate of Staten Island are {}, {}.'.format(brlatitude, brlongitude))

The geograpical coordinate of Staten Island are 40.6501038, -73.9495823.


A picture says a thousand words, so lets create a map using Folium and superimpose the Brooklyn data alone

In [88]:
map_br = folium.Map(location=[brlatitude, brlongitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(br_data['Latitude'], br_data['Longitude'], br_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_br)  
    
map_br

Lets reuse the function we created for Brooklyn but this time around we are going to get the Top 100 venues and within the radius of 500 meters of each neighborhood in Brooklyn

In [89]:
# type your answer here
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

br_venues = getNearbyVenues(names=br_data['Neighborhood'],
                                   latitudes=br_data['Latitude'],
                                   longitudes=br_data['Longitude']
                                  )

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


#### Lets check the size of this dataframe

In [90]:
print(br_venues.shape)
br_venues.head()

(2700, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Bay Ridge              40.625801              -74.030621   
1    Bay Ridge              40.625801              -74.030621   
2    Bay Ridge              40.625801              -74.030621   
3    Bay Ridge              40.625801              -74.030621   
4    Bay Ridge              40.625801              -74.030621   

                         Venue  Venue Latitude  Venue Longitude  \
0  Pilo Arts Day Spa and Salon       40.624748       -74.030591   
1                    Bagel Boy       40.627896       -74.029335   
2          Leo's Casa Calamari       40.624200       -74.030931   
3                Cocoa Grinder       40.623967       -74.030863   
4                 Pegasus Cafe       40.623168       -74.031186   

   Venue Category  
0             Spa  
1      Bagel Shop  
2     Pizza Place  
3       Juice Bar  
4  Breakfast Spot

Grouping the Venues by Neighborhood

In [91]:
br_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Bath Beach                                    47                      47   
Bay Ridge                                     87                      87   
Bedford Stuyvesant                            27                      27   
Bensonhurst                                   32                      32   
Bergen Beach                                   6                       6   
Boerum Hill                                   92                      92   
Borough Park                                  21                      21   
Brighton Beach                                45                      45   
Broadway Junction                             23                      23   
Brooklyn Heights                             100                     100   
Brownsville                                   19                      19   
Bushwick                                      78                      78   
Canarsie                                       7                       7   
Carroll Gardens                              100                     100   
City Line                                     35                      35   
Clinton Hill                                  99                      99   
Cobble Hill                                   93                      93   
Coney Island                                  16                      16   
Crown Heights                                 23                      23   
Cypress Hills                                 28                      28   
Ditmas Park                                   47                      47   
Downtown                                      87                      87   
Dumbo                                         53                      53   
Dyker Heights                                  6                       6   
East Flatbush                                 14                      14   
East New York                                 11                      11   
East Williamsburg                             71                      71   
Erasmus                                       20                      20   
Flatbush                                      20                      20   
Flatlands                                     18                      18   
Fort Greene                                   56                      56   
Fort Hamilton                                 70                      70   
Fulton Ferry                                  55                      55   
Georgetown                                    30                      30   
Gerritsen Beach                               20                      20   
Gowanus                                       64                      64   
Gravesend                                     25                      25   
Greenpoint                                    84                      84   
Highland Park                                 17                      17   
Homecrest                                     39                      39   
Kensington                                    38                      38   
Madison                                       11                      11   
Manhattan Beach                               11                      11   
Manhattan Terrace                             23                      23   
Marine Park                                   10                      10   
Midwood                                       12                      12   
Mill Basin                                    38                      38   
Mill Island                                    1                       1   
New Lots                                      21                      21   
North Side                                   100                     100   
Ocean Hill                                    29                      29   

In [92]:
print('There are {} uniques categories.'.format(len(br_venues['Venue Category'].unique())))

There are 290 uniques categories.


#### Lets analyze each neighborhood in Brooklyn

In [93]:
# one hot encoding
br_onehot = pd.get_dummies(br_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
br_onehot['Neighborhood'] = br_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [br_onehot.columns[-1]] + list(br_onehot.columns[:-1])
br_onehot = br_onehot[fixed_columns]

br_onehot.head()

Yoga Studio  Accessories Store  Airport Terminal  American Restaurant  \
0            0                  0                 0                    0   
1            0                  0                 0                    0   
2            0                  0                 0                    0   
3            0                  0                 0                    0   
4            0                  0                 0                    0   

   Animal Shelter  Antique Shop  Arepa Restaurant  Argentinian Restaurant  \
0               0             0                 0                       0   
1               0             0                 0                       0   
2               0             0                 0                       0   
3               0             0                 0                       0   
4               0             0                 0                       0   

   Art Gallery  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0            0                    0                     0                 0   
1            0                    0                     0                 0   
2            0                    0                     0                 0   
3            0                    0                     0                 0   
4            0                    0                     0                 0   

   Athletics & Sports  Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                   0            0          0           0       0     0    0   
1                   0            0          0           1       0     0    0   
2                   0            0          0           0       0     0    0   
3                   0            0          0           0       0     0    0   
4                   0            0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Beach  Beer Bar  \
0               0                 0                 0      0         0   
1               0                 0                 0      0         0   
2               0                 0                 0      0         0   
3               0                 0                 0      0         0   
4               0                 0                 0      0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0            0           0              0                         0   
1            0           0              0                         0   
2            0           0              0                         0   
3            0           0              0                         0   
4            0           0              0                         0   

   Bike Shop  Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0          0       0           0              0          0         0   
1          0       0           0              0          0         0   
2          0       0           0              0          0         0   
3          0       0           0              0          0         0   
4          0       0           0              0          0         0   

   Boxing Gym  Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  \
0           0               0        0            0       0                0   
1           0               0        0            0       0                0   
2           0               0        0            0       0                0   
3           0               0        0            0       0                0   
4           0               1        0            0       0                0   

   Buffet  Burger Joint  Burmese Restaurant  Burrito Place  Bus Line  \
0       0             0                   0              0         0   
1       0             0                   0              0         0   
2       0             0                   0              0         0   
3       0             0                   0          

In [94]:
br_onehot.shape

(2700, 290)

#### Lets group the rows by Neighborhood and by taking the mean of the frequency of occurance of each category

In [95]:
br_grouped = br_onehot.groupby('Neighborhood').mean().reset_index()
br_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                  Bath Beach     0.000000           0.000000   
1                   Bay Ridge     0.000000           0.000000   
2          Bedford Stuyvesant     0.000000           0.000000   
3                 Bensonhurst     0.000000           0.000000   
4                Bergen Beach     0.000000           0.000000   
5                 Boerum Hill     0.021739           0.000000   
6                Borough Park     0.000000           0.000000   
7              Brighton Beach     0.000000           0.000000   
8           Broadway Junction     0.000000           0.000000   
9            Brooklyn Heights     0.040000           0.000000   
10                Brownsville     0.000000           0.000000   
11                   Bushwick     0.000000           0.000000   
12                   Canarsie     0.000000           0.000000   
13            Carroll Gardens     0.000000           0.000000   
14                  City Line     0.000000           0.000000   
15               Clinton Hill     0.030303           0.000000   
16                Cobble Hill     0.032258           0.000000   
17               Coney Island     0.000000           0.000000   
18              Crown Heights     0.000000           0.000000   
19              Cypress Hills     0.000000           0.000000   
20                Ditmas Park     0.021277           0.000000   
21                   Downtown     0.011494           0.000000   
22                      Dumbo     0.037736           0.000000   
23              Dyker Heights     0.000000           0.000000   
24              East Flatbush     0.000000           0.000000   
25              East New York     0.000000           0.000000   
26          East Williamsburg     0.000000           0.000000   
27                    Erasmus     0.050000           0.000000   
28                   Flatbush     0.000000           0.000000   
29                  Flatlands     0.000000           0.000000   
30                Fort Greene     0.035714           0.000000   
31              Fort Hamilton     0.000000           0.000000   
32               Fulton Ferry     0.000000           0.000000   
33                 Georgetown     0.000000           0.000000   
34            Gerritsen Beach     0.000000           0.000000   
35                    Gowanus     0.015625           0.000000   
36                  Gravesend     0.000000           0.000000   
37                 Greenpoint     0.035714           0.000000   
38              Highland Park     0.000000           0.000000   
39                  Homecrest     0.000000           0.000000   
40                 Kensington     0.000000           0.000000   
41                    Madison     0.000000           0.000000   
42            Manhattan Beach     0.000000           0.000000   
43          Manhattan Terrace     0.000000           0.000000   
44                Marine Park     0.000000           0.000000   
45                    Midwood     0.000000           0.000000   
46                 Mill Basin     0.000000           0.000000   
47                Mill Island     0.000000           0.000000   
48                   New Lots     0.000000           0.000000   
49                 North Side     0.050000           0.000000   
50                 Ocean Hill     0.000000           0.000000   
51              Ocean Parkway     0.000000           0.000000   
52            Paerdegat Basin     0.000000           0.000000   
53                 Park Slope     0.017857           0.017857   
54           Prospect Heights     0.000000           0.000000   
55  Prospect Lefferts Gardens     0.000000           0.000000   
56        Prospect Park South     0.000000           0.000000   
57                   Red Hook     0.000000           0.000000   
58             Remsen Village     0.000000           0.000000   
59                      Rugby     0.000000           0.000000   
60                   Sea Gate     0.000000          

In [96]:
br_grouped.shape

(70, 290)

#####  Printing each neighborhood along with the top 5 most common venues

In [97]:
num_top_venues = 5

for hood in br_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = br_grouped[br_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                  venue  freq
0    Chinese Restaurant  0.11
1              Pharmacy  0.06
2    Italian Restaurant  0.04
3       Bubble Tea Shop  0.04
4  Fast Food Restaurant  0.04


----Bay Ridge----
                 venue  freq
0          Pizza Place  0.06
1   Italian Restaurant  0.06
2                  Spa  0.06
3  American Restaurant  0.03
4   Chinese Restaurant  0.03


----Bedford Stuyvesant----
           venue  freq
0           Café  0.07
1    Coffee Shop  0.07
2    Pizza Place  0.07
3  Deli / Bodega  0.07
4            Bar  0.07


----Bensonhurst----
                venue  freq
0  Chinese Restaurant  0.09
1    Sushi Restaurant  0.06
2          Donut Shop  0.06
3       Grocery Store  0.06
4      Ice Cream Shop  0.06


----Bergen Beach----
                venue  freq
0     Harbor / Marina  0.33
1      Baseball Field  0.17
2          Donut Shop  0.17
3          Playground  0.17
4  Athletics & Sports  0.17


----Boerum Hill----
            venue  freq
0     Coffee 

##### Putting this in a pandas dataframe

In [98]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]



Creating a dataframe and displaying the top 10 venues in each neighborhood

In [99]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = br_grouped['Neighborhood']

for ind in np.arange(br_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(br_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach    Chinese Restaurant              Pharmacy   
1           Bay Ridge                   Spa           Pizza Place   
2  Bedford Stuyvesant         Deli / Bodega           Pizza Place   
3         Bensonhurst    Chinese Restaurant    Italian Restaurant   
4        Bergen Beach       Harbor / Marina        Baseball Field   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Gas Station       Bubble Tea Shop      Sushi Restaurant   
1    Italian Restaurant    Chinese Restaurant   American Restaurant   
2                  Café           Coffee Shop                   Bar   
3      Sushi Restaurant        Ice Cream Shop            Donut Shop   
4            Playground            Donut Shop    Athletics & Sports   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    Italian Restaurant  Fast Food Restaurant    Dim Sum Restaurant   
1      Greek Restaurant        Cosmetics Shop                   Bar   
2             Gift Shop   Japanese Restaurant             Juice Bar   
3         Grocery Store            Bagel Shop               Factory   
4         Event Service           Event Space               Factory   

  9th Most Common Venue 10th Most Common Venue  
0          Dessert Shop         Sandwich Place  
1         Grocery Store             Bagel Shop  
2              Boutique    Fried Chicken Joint  
3          Liquor Store         Cha Chaan Teng  
4    Falafel Restaurant                   Farm

### Cluster the neighborhoods in Brooklyn using K-Means

In [100]:
# set number of clusters
kclusters = 5

br_grouped_clustering = br_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(br_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [101]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

br_merged = br_data

br_merged = br_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

br_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Brooklyn    Bay Ridge  40.625801 -74.030621               0   
1  Brooklyn  Bensonhurst  40.611009 -73.995180               0   
2  Brooklyn  Sunset Park  40.645103 -74.010316               0   
3  Brooklyn   Greenpoint  40.730201 -73.954241               0   
4  Brooklyn    Gravesend  40.595260 -73.973471               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   Spa           Pizza Place    Italian Restaurant   
1    Chinese Restaurant    Italian Restaurant      Sushi Restaurant   
2                Bakery           Pizza Place         Deli / Bodega   
3           Pizza Place           Coffee Shop          Cocktail Bar   
4    Chinese Restaurant           Bus Station           Pizza Place   

  4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
0    Chinese Restaurant   American Restaurant           Greek Restaurant   
1        Ice Cream Shop            Donut Shop              Grocery Store   
2                  Bank    Mexican Restaurant  Latin American Restaurant   
3                   Bar           Yoga Studio              Deli / Bodega   
4                Lounge                Bakery                Men's Store   

  7th Most Common Venue 8th Most Common Venue    9th Most Common Venue  \
0        Cosmetics Shop                   Bar            Grocery Store   
1            Bagel Shop               Factory             Liquor Store   
2   Fried Chicken Joint     Mobile Phone Shop                      Gym   
3      Sushi Restaurant           Record Shop  New American Restaurant   
4            Donut Shop         Metro Station              Fish Market   

  10th Most Common Venue  
0             Bagel Shop  
1         Cha Chaan Teng  
2     Italian Restaurant  
3          Grocery Store  
4      Martial Arts Dojo

#### Examining the clusters

#### Cluster 1

In [102]:
br_merged.loc[br_merged['Cluster Labels'] == 0, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
0                   Bay Ridge                   Spa   
1                 Bensonhurst    Chinese Restaurant   
2                 Sunset Park                Bakery   
3                  Greenpoint           Pizza Place   
4                   Gravesend    Chinese Restaurant   
5              Brighton Beach                 Beach   
6              Sheepshead Bay    Turkish Restaurant   
7           Manhattan Terrace           Pizza Place   
8                    Flatbush           Coffee Shop   
9               Crown Heights           Pizza Place   
11                 Kensington         Grocery Store   
12            Windsor Terrace                 Diner   
13           Prospect Heights                   Bar   
15               Williamsburg           Coffee Shop   
16                   Bushwick         Deli / Bodega   
17         Bedford Stuyvesant         Deli / Bodega   
18           Brooklyn Heights           Yoga Studio   
19                Cobble Hill            Playground   
20            Carroll Gardens    Italian Restaurant   
21                   Red Hook    Seafood Restaurant   
22                    Gowanus                   Bar   
23                Fort Greene    Italian Restaurant   
24                 Park Slope           Coffee Shop   
25              Cypress Hills   Fried Chicken Joint   
27              Starrett City           Bus Station   
31            Manhattan Beach                  Café   
33                 Bath Beach    Chinese Restaurant   
34               Borough Park                  Bank   
36            Gerritsen Beach                   Bar   
37                Marine Park           Pizza Place   
38               Clinton Hill           Pizza Place   
40                   Downtown          Burger Joint   
41                Boerum Hill          Dance Studio   
42  Prospect Lefferts Gardens         Deli / Bodega   
43                 Ocean Hill         Deli / Bodega   
44                  City Line            Donut Shop   
45               Bergen Beach       Harbor / Marina   
46                    Midwood           Pizza Place   
48                 Georgetown                  Bank   
49          East Williamsburg                   Bar   
50                 North Side           Coffee Shop   
51                 South Side                   Bar   
52              Ocean Parkway            Donut Shop   
53              Fort Hamilton         Deli / Bodega   
54                Ditmas Park         Deli / Bodega   
60                 Mill Basin    Chinese Restaurant   
61               Fulton Ferry                  Park   
62               Vinegar Hill            Food Truck   
63                 Weeksville        Discount Store   
64          Broadway Junction                 Diner   
65                      Dumbo                  Park   
66                  Homecrest                  Bank   
68                    Madison         Deli / Bodega   

          2nd Most Common Venue  3rd Most Common Venue  \
0                   Pizza Place     Italian Restaurant   
1            Italian Restaurant       Sushi Restaurant   
2                   Pizza Place          Deli / Bodega   
3                   Coffee Shop           Cocktail Bar   
4                   Bus Station            Pizza Place   
5   Eastern European Restaurant     Russian Restaurant   
6                  Dessert Shop          Boat or Ferry   
7                    Donut Shop          Deli / Bodega   
8          Caribbean Restaurant     Mexican Restaurant   
9                        Museum                   Café   
11              Thai Restaurant            Pizza Place   
12                Deli / Bodega                   Park   
13           Mexican Restaurant           Cocktail Bar   
15                          Bar             Bagel Shop   
16                          Bar     Mexican Restaurant   
17                  Pizza Place                   Café   
18                Deli / Bodega                   Park   
19

#### Cluster 2

In [103]:
br_merged.loc[br_merged['Cluster Labels'] == 1, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
30  Mill Island                  Pool         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
30  Ethiopian Restaurant         Event Service           Event Space   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
30               Factory    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
30        Farmers Market   Fast Food Restaurant

#### Cluster 3

In [104]:
br_merged.loc[br_merged['Cluster Labels'] == 2, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
10  East Flatbush    Chinese Restaurant                  Food   
14    Brownsville                  Park            Restaurant   
35  Dyker Heights                 Plaza                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
10           Supermarket                  Park  Fast Food Restaurant   
14    Chinese Restaurant      Airport Terminal            Playground   
35          Dance Studio          Burger Joint            Bagel Shop   

   6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
10         Moving Target              Pharmacy         Hardware Store   
14              Pharmacy          Burger Joint  Performing Arts Venue   
35           Golf Course  Ethiopian Restaurant          Event Service   

   9th Most Common Venue 10th Most Common Venue  
10            Print Shop      Food & Drink Shop  
14           Pizza Place     Spanish Restaurant  
35           Event Space                Factory

#### Cluster 4

In [105]:
br_merged.loc[br_merged['Cluster Labels'] == 3, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
39     Sea Gate           Bus Station                 Beach   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
39                   Spa          Home Service     Food & Drink Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
39        Farmers Market         Event Service           Event Space   

   9th Most Common Venue 10th Most Common Venue  
39               Factory     Falafel Restaurant

#### Cluster 5

In [106]:
br_merged.loc[br_merged['Cluster Labels'] == 4, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
26        East New York    Salon / Barbershop           Pizza Place   
28             Canarsie  Caribbean Restaurant      Asian Restaurant   
29            Flatlands              Pharmacy  Caribbean Restaurant   
32         Coney Island      Baseball Stadium  Caribbean Restaurant   
47  Prospect Park South  Caribbean Restaurant           Pizza Place   
55              Wingate   Fried Chicken Joint  Fast Food Restaurant   
56                Rugby  Caribbean Restaurant                  Bank   
57       Remsen Village  Caribbean Restaurant  Fast Food Restaurant   
58             New Lots    Chinese Restaurant         Grocery Store   
59      Paerdegat Basin                  Food       Harbor / Marina   
67        Highland Park    Spanish Restaurant           Pizza Place   
69              Erasmus  Caribbean Restaurant         Grocery Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
26                 Plaza         Event Service     Convenience Store   
28         Grocery Store                   Gym    Chinese Restaurant   
29  Fast Food Restaurant   Fried Chicken Joint   Arts & Crafts Store   
32               Brewery        Clothing Store   Monument / Landmark   
47  Fast Food Restaurant     Mobile Phone Shop         Grocery Store   
55                  Park            Donut Shop             BBQ Joint   
56         Grocery Store           Pizza Place                 Diner   
57         Deli / Bodega            Donut Shop           Fish Market   
58   Fried Chicken Joint           Pizza Place            Playground   
59         Moving Target           Auto Garage      Asian Restaurant   
67         Metro Station         Grocery Store  Gym / Fitness Center   
69           Yoga Studio             Juice Bar              Pharmacy   

   6th Most Common Venue   7th Most Common Venue  \
26            Food Truck           Metro Station   
28        Shipping Store         Thai Restaurant   
29     Electronics Store                  Lounge   
32           Pizza Place              Food Court   
47   Fried Chicken Joint      Mexican Restaurant   
55             Nightclub    Gym / Fitness Center   
56  Fast Food Restaurant     Fried Chicken Joint   
57        Breakfast Spot             Supermarket   
58                  Park                    Bank   
59         Women's Store             Event Space   
67   Fried Chicken Joint  Furniture / Home Store   
69     Convenience Store              Donut Shop   

            8th Most Common Venue      9th Most Common Venue  \
26           Caribbean Restaurant        Fried Chicken Joint   
28          Entertainment Service       Ethiopian Restaurant   
29  Paper / Office Supplies Store                        Bar   
32                   Skating Rink             Farmers Market   
47                     Donut Shop  Latin American Restaurant   
55                    Bus Station               Intersection   
56             Seafood Restaurant             Sandwich Place   
57            Fried Chicken Joint                       Café   
58                         Bakery             Breakfast Spot   
59                        Factory         Falafel Restaurant   
67                  Big Box Store                     Garden   
69                         School                Music Venue   

   10th Most Common Venue  
26            Bus Station  
28          Event Service  
29            Video Store  
32            Music Venue  
47             Food Truck  
55               Pharmacy  
56      Mobile Phone Shop  
57         Sandwich Place  
58     Salon / Barbershop  
59                   Farm  
67           Tennis Court  
69               Bus Line

#### Visualizing the clusters

In [107]:
# create map
brmap_clusters = folium.Map(location=[brlatitude, brlongitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(br_merged['Latitude'], br_merged['Longitude'], br_merged['Neighborhood'], br_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(brmap_clusters)
       
brmap_clusters

#### Completion of Analysis for Brooklyn

We have now completed the analysis and clustering for Brooklyn and this would now help Mr.John take an informed decision if he wishes to relocate to any of the neighborhoods in Brooklyn.

However our analysis is still not complete. Remember there are other Boroughs in New York and we have not done any analysis on those. We will now proceed to do similar analysis for each of the other Boroughs so that Mr.John has all of the required information to make an informed Decision.

### Let us now proceed onto Bronx do similar analysis and clustering of those neighborhoods

Lets now create a new Dataframe which has only Bronx neighborhoods

In [20]:
bx_data = neighborhoods[neighborhoods['Borough'] == 'Bronx'].reset_index(drop=True)
bx_data.head(500)

Borough         Neighborhood   Latitude  Longitude
0    Bronx            Wakefield  40.894705 -73.847201
1    Bronx           Co-op City  40.874294 -73.829939
2    Bronx          Eastchester  40.887556 -73.827806
3    Bronx            Fieldston  40.895437 -73.905643
4    Bronx            Riverdale  40.890834 -73.912585
5    Bronx          Kingsbridge  40.881687 -73.902818
6    Bronx             Woodlawn  40.898273 -73.867315
7    Bronx              Norwood  40.877224 -73.879391
8    Bronx       Williamsbridge  40.881039 -73.857446
9    Bronx           Baychester  40.866858 -73.835798
10   Bronx       Pelham Parkway  40.857413 -73.854756
11   Bronx          City Island  40.847247 -73.786488
12   Bronx         Bedford Park  40.870185 -73.885512
13   Bronx   University Heights  40.855727 -73.910416
14   Bronx       Morris Heights  40.847898 -73.919672
15   Bronx              Fordham  40.860997 -73.896427
16   Bronx         East Tremont  40.842696 -73.887356
17   Bronx           West Farms  40.839475 -73.877745
18   Bronx         High  Bridge  40.836623 -73.926102
19   Bronx              Melrose  40.819754 -73.909422
20   Bronx           Mott Haven  40.806239 -73.916100
21   Bronx          Port Morris  40.801664 -73.913221
22   Bronx             Longwood  40.815099 -73.895788
23   Bronx          Hunts Point  40.809730 -73.883315
24   Bronx           Morrisania  40.823592 -73.901506
25   Bronx            Soundview  40.821012 -73.865746
26   Bronx         Clason Point  40.806551 -73.854144
27   Bronx          Throgs Neck  40.815109 -73.816350
28   Bronx         Country Club  40.844246 -73.824099
29   Bronx          Parkchester  40.837938 -73.856003
30   Bronx   Westchester Square  40.840619 -73.842194
31   Bronx             Van Nest  40.843608 -73.866299
32   Bronx          Morris Park  40.847549 -73.850402
33   Bronx              Belmont  40.857277 -73.888452
34   Bronx       Spuyten Duyvil  40.881395 -73.917190
35   Bronx      North Riverdale  40.908543 -73.904531
36   Bronx           Pelham Bay  40.850641 -73.832074
37   Bronx        Schuylerville  40.826580 -73.826203
38   Bronx       Edgewater Park  40.821986 -73.813885
39   Bronx          Castle Hill  40.819014 -73.848027
40   Bronx            Olinville  40.871371 -73.863324
41   Bronx       Pelham Gardens  40.862966 -73.841612
42   Bronx            Concourse  40.834284 -73.915589
43   Bronx            Unionport  40.829774 -73.850535
44   Bronx             Edenwald  40.884561 -73.848083
45   Bronx    Claremont Village  40.831428 -73.901199
46   Bronx    Concourse Village  40.824780 -73.915847
47   Bronx           Mount Eden  40.843826 -73.916556
48   Bronx           Mount Hope  40.848842 -73.908299
49   Bronx            Bronxdale  40.852723 -73.861726
50   Bronx             Allerton  40.865788 -73.859319
51   Bronx  Kingsbridge Heights  40.870392 -73.901523

Lets also get the Latitude and Longitude co-ordinates for Bronx using the geopy library

In [21]:
address = 'Bronx, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
bxlatitude = location.latitude
bxlongitude = location.longitude
print('The geograpical coordinate of Bronx are {}, {}.'.format(bxlatitude, bxlongitude))

The geograpical coordinate of Bronx are 40.8466508, -73.8785937.


A picture says a thousand words, so lets create a map using Folium and superimpose the Bronx data alone

In [22]:
map_bx = folium.Map(location=[bxlatitude, bxlongitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(bx_data['Latitude'], bx_data['Longitude'], bx_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_bx)  
    
map_bx

Lets reuse the function we created earlier for Bronx but this time around we are going to get the Top 100 venues and within the radius of 500 meters of each neighborhood in Bronx

In [23]:
# type your answer here
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

bx_venues = getNearbyVenues(names=bx_data['Neighborhood'],
                                   latitudes=bx_data['Latitude'],
                                   longitudes=bx_data['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Claremont Village
Concourse Village
Mount Eden
Mount Hope
Bronxdale
Allerton
Kingsbridge Heights


#### Lets check the size of this dataframe

In [24]:
print(bx_venues.shape)
bx_venues.head()

(1216, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896528       -73.844700        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

Grouping the Venues by Neighborhood

In [25]:
bx_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Allerton                                31                      31     31   
Baychester                              19                      19     19   
Bedford Park                            35                      35     35   
Belmont                                100                     100    100   
Bronxdale                               13                      13     13   
Castle Hill                              8                       8      8   
City Island                             27                      27     27   
Claremont Village                       15                      15     15   
Clason Point                            10                      10     10   
Co-op City                              17                      17     17   
Concourse                               29                      29     29   
Concourse Village                       43                      43     43   
Country Club                             5                       5      5   
East Tremont                            17                      17     17   
Eastchester                             21                      21     21   
Edenwald                                 6                       6      6   
Edgewater Park                          21                      21     21   
Fieldston                                3                       3      3   
Fordham                                 85                      85     85   
High  Bridge                            24                      24     24   
Hunts Point                             12                      12     12   
Kingsbridge                             71                      71     71   
Kingsbridge Heights                     30                      30     30   
Longwood                                 8                       8      8   
Melrose                                 26                      26     26   
Morris Heights                           8                       8      8   
Morris Park                             23                      23     23   
Morrisania                              26                      26     26   
Mott Haven                              22                      22     22   
Mount Eden                              31                      31     31   
Mount Hope                              11                      11     11   
North Riverdale                         24                      24     24   
Norwood                                 34                      34     34   
Olinville                               10                      10     10   
Parkchester                             33                      33     33   
Pelham Bay                              39                      39     39   
Pelham Gardens                          22                      22     22   
Pelham Parkway                          23                      23     23   
Port Morris                             13                      13     13   
Riverdale                               11                      11     11   
Schuylerville                           18                      18     18   
Soundview                               15                      15     15   
Spuyten Duyvil                          10                      10     10   
Throgs Neck                             10                      10     10   
Unionport                               23                      23     23   
University Heights                      20                      20     20   
Van Nest                                19                      19     19   
Wakefield                                9                       9      9   
West Farms                              19                      19     19   
Westchester Square                      33                      33     33   
Williamsbridge   

In [26]:
print('There are {} uniques categories.'.format(len(bx_venues['Venue Category'].unique())))

There are 171 uniques categories.


#### Lets analyze each neighborhood in Bronx

In [27]:
# one hot encoding
bx_onehot = pd.get_dummies(bx_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
bx_onehot['Neighborhood'] = bx_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [bx_onehot.columns[-1]] + list(bx_onehot.columns[:-1])
bx_onehot = bx_onehot[fixed_columns]

bx_onehot.head()

Neighborhood  Accessories Store  African Restaurant  American Restaurant  \
0    Wakefield                  0                   0                    0   
1    Wakefield                  0                   0                    0   
2    Wakefield                  0                   0                    0   
3    Wakefield                  0                   0                    0   
4    Wakefield                  0                   0                    0   

   Arcade  Arepa Restaurant  Art Gallery  Art Museum  Asian Restaurant  \
0       0                 0            0           0                 0   
1       0                 0            0           0                 0   
2       0                 0            0           0                 0   
3       0                 0            0           0                 0   
4       0                 0            0           0                 0   

   Athletics & Sports  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                   0          0           0       0     0    0   
1                   0          0           0       0     0    0   
2                   0          0           0       0     0    0   
3                   0          0           0       0     0    0   
4                   0          0           0       0     0    0   

   Baseball Field  Basketball Court  Beer Bar  Board Shop  Boat or Ferry  \
0               0                 0         0           0              0   
1               0                 0         0           0              0   
2               0                 0         0           0              0   
3               0                 0         0           0              0   
4               0                 0         0           0              0   

   Bookstore  Bowling Alley  Breakfast Spot  Brewery  Buffet  Building  \
0          0              0               0        0       0         0   
1          0              0               0        0       0         0   
2          0              0               0        0       0         0   
3          0              0               0        0       0         0   
4          0              0               0        0       0         0   

   Burger Joint  Bus Line  Bus Station  Bus Stop  Café  Candy Store  \
0             0         0            0         0     0            0   
1             0         0            0         0     0            0   
2             0         0            0         0     0            0   
3             0         0            0         0     0            0   
4             0         0            0         0     0            0   

   Caribbean Restaurant  Check Cashing Service  Cheese Shop  \
0                     0                      0            0   
1                     0                      0            0   
2                     0                      0            0   
3                     0                      0            0   
4                     0                      0            0   

   Chinese Restaurant  Clothing Store  Coffee Shop  Comfort Food Restaurant  \
0                   0               0            0                        0   
1                   0               0            0                        0   
2                   0               0            0                        0   
3                   0               0            0                        0   
4                   0               0            0                        0   

   Comic Shop  Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0           0                           0                  0               0   
1           0                           0                  0               0   
2           0                           0                  0               0   
3           0                           0                  0               0   
4           0                           0                  0               0   

   Dance Studio  Deli

In [28]:
bx_onehot.shape

(1216, 172)

#### Lets group the rows by Neighborhood and by taking the mean of the frequency of occurance of each category

In [29]:
bx_grouped = bx_onehot.groupby('Neighborhood').mean().reset_index()
bx_grouped

Neighborhood  Accessories Store  African Restaurant  \
0              Allerton           0.000000            0.000000   
1            Baychester           0.000000            0.000000   
2          Bedford Park           0.000000            0.000000   
3               Belmont           0.000000            0.000000   
4             Bronxdale           0.000000            0.000000   
5           Castle Hill           0.000000            0.000000   
6           City Island           0.000000            0.000000   
7     Claremont Village           0.000000            0.000000   
8          Clason Point           0.000000            0.000000   
9            Co-op City           0.000000            0.000000   
10            Concourse           0.000000            0.000000   
11    Concourse Village           0.000000            0.000000   
12         Country Club           0.000000            0.000000   
13         East Tremont           0.000000            0.000000   
14          Eastchester           0.000000            0.000000   
15             Edenwald           0.000000            0.000000   
16       Edgewater Park           0.000000            0.000000   
17            Fieldston           0.000000            0.000000   
18              Fordham           0.011765            0.011765   
19         High  Bridge           0.000000            0.000000   
20          Hunts Point           0.000000            0.000000   
21          Kingsbridge           0.000000            0.000000   
22  Kingsbridge Heights           0.000000            0.000000   
23             Longwood           0.000000            0.000000   
24              Melrose           0.000000            0.000000   
25       Morris Heights           0.000000            0.000000   
26          Morris Park           0.000000            0.000000   
27           Morrisania           0.000000            0.000000   
28           Mott Haven           0.000000            0.000000   
29           Mount Eden           0.000000            0.000000   
30           Mount Hope           0.000000            0.000000   
31      North Riverdale           0.000000            0.000000   
32              Norwood           0.000000            0.000000   
33            Olinville           0.000000            0.000000   
34          Parkchester           0.000000            0.000000   
35           Pelham Bay           0.000000            0.000000   
36       Pelham Gardens           0.000000            0.000000   
37       Pelham Parkway           0.000000            0.000000   
38          Port Morris           0.000000            0.000000   
39            Riverdale           0.000000            0.000000   
40        Schuylerville           0.000000            0.000000   
41            Soundview           0.000000            0.000000   
42       Spuyten Duyvil           0.000000            0.000000   
43          Throgs Neck           0.000000            0.000000   
44            Unionport           0.000000            0.000000   
45   University Heights           0.000000            0.050000   
46             Van Nest           0.000000            0.000000   
47            Wakefield           0.000000            0.000000   
48           West Farms           0.000000            0.000000   
49   Westchester Square           0.000000            0.000000   
50       Williamsbridge           0.000000            0.000000   
51             Woodlawn           0.000000            0.000000   

    American Restaurant    Arcade  Arepa Restaurant  Art Gallery  Art Museum  \
0              0.000000  0.000000          0.000000     0.000000    0.000000   
1              0.000000  0.052632          0.000000     0.000000    0.000000   
2              0.000000  0.000000          0.000000     0.000000    0.000000   
3              0.010000  0.000000          0.000000     0.000000    0.000000   
4              0.000000  0.000000          0.000000     0.000000    0.000000   
5              0.000000  0.00000

In [30]:
bx_grouped.shape

(52, 172)

#####  Printing each neighborhood along with the top 5 most common venues

In [31]:
num_top_venues = 5

for hood in bx_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = bx_grouped[bx_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
              venue  freq
0       Pizza Place  0.16
1     Deli / Bodega  0.10
2  Department Store  0.06
3    Cosmetics Shop  0.06
4       Supermarket  0.06


----Baychester----
                  venue  freq
0            Donut Shop  0.11
1        Discount Store  0.05
2  Fast Food Restaurant  0.05
3    Spanish Restaurant  0.05
4           Supermarket  0.05


----Bedford Park----
                venue  freq
0  Chinese Restaurant  0.14
1               Diner  0.11
2  Mexican Restaurant  0.09
3         Pizza Place  0.09
4  Spanish Restaurant  0.06


----Belmont----
                venue  freq
0  Italian Restaurant  0.18
1         Pizza Place  0.09
2       Deli / Bodega  0.08
3              Bakery  0.05
4          Donut Shop  0.03


----Bronxdale----
                   venue  freq
0            Coffee Shop  0.08
1                   Park  0.08
2     Chinese Restaurant  0.08
3  Performing Arts Venue  0.08
4     Spanish Restaurant  0.08


----Castle Hill----
            venue  fr

##### Putting this in a pandas dataframe

In [32]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]



Creating a dataframe and displaying the top 10 venues in each neighborhood

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = bx_grouped['Neighborhood']

for ind in np.arange(bx_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(bx_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue          2nd Most Common Venue  \
0      Allerton           Pizza Place                  Deli / Bodega   
1    Baychester            Donut Shop           Other Great Outdoors   
2  Bedford Park    Chinese Restaurant                          Diner   
3       Belmont    Italian Restaurant                    Pizza Place   
4     Bronxdale        Breakfast Spot  Paper / Office Supplies Store   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
0      Department Store        Cosmetics Shop                  Supermarket   
1        Sandwich Place   Fried Chicken Joint            Electronics Store   
2           Pizza Place    Mexican Restaurant               Sandwich Place   
3         Deli / Bodega                Bakery                Grocery Store   
4    Spanish Restaurant           Supermarket  Eastern European Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Dessert Shop        Discount Store    Chinese Restaurant   
1                  Bank        Mattress Store    Spanish Restaurant   
2         Deli / Bodega    Spanish Restaurant                   Bar   
3          Dessert Shop            Donut Shop                  Bank   
4    Mexican Restaurant    Chinese Restaurant           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
0   Fried Chicken Joint   Fast Food Restaurant  
1             Pet Store            Men's Store  
2            Food Truck    Fried Chicken Joint  
3           Fish Market         Sandwich Place  
4                  Bank  Performing Arts Venue

### Cluster the neighborhoods in Bronx using K-Means

In [34]:
# set number of clusters
kclusters = 5

bx_grouped_clustering = bx_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(bx_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 2, 4, 1, 4, 1, 4, 4, 4, 4], dtype=int32)

In [35]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

bx_merged = bx_data

bx_merged = bx_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

bx_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               2   
1   Bronx   Co-op City  40.874294 -73.829939               4   
2   Bronx  Eastchester  40.887556 -73.827806               2   
3   Bronx    Fieldston  40.895437 -73.905643               0   
4   Bronx    Riverdale  40.890834 -73.912585               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy        Ice Cream Shop            Laundromat   
1           Bus Station            Restaurant         Grocery Store   
2  Caribbean Restaurant         Deli / Bodega                 Diner   
3                 Plaza           Bus Station                 River   
4                  Park  Medical Supply Store                 Plaza   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0           Gas Station  Caribbean Restaurant            Donut Shop   
1              Pharmacy  Fast Food Restaurant   Fried Chicken Joint   
2              Bus Stop           Bus Station         Metro Station   
3            Donut Shop           Flower Shop           Fish Market   
4                   Gym           Bus Station            Food Truck   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Sandwich Place          Dessert Shop              Dive Bar   
1        Mattress Store      Basketball Court        Baseball Field   
2           Pizza Place              Platform     Convenience Store   
3     Fish & Chips Shop  Fast Food Restaurant        Farmers Market   
4                  Bank            Playground          Home Service   

  10th Most Common Venue  
0        Doctor's Office  
1             Bagel Shop  
2             Donut Shop  
3      Electronics Store  
4      Fish & Chips Shop

#### Examining the clusters

#### Cluster 1

In [36]:
bx_merged.loc[bx_merged['Cluster Labels'] == 0, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
3    Fieldston                 Plaza           Bus Station   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
3                 River            Donut Shop           Flower Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3           Fish Market     Fish & Chips Shop  Fast Food Restaurant   

  9th Most Common Venue 10th Most Common Venue  
3        Farmers Market      Electronics Store

#### Cluster 2

In [37]:
bx_merged.loc[bx_merged['Cluster Labels'] == 1, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
6          Woodlawn           Pizza Place         Deli / Bodega   
10   Pelham Parkway           Pizza Place    Italian Restaurant   
16     East Tremont           Pizza Place        Breakfast Spot   
27      Throgs Neck         Deli / Bodega           Pizza Place   
31         Van Nest         Deli / Bodega           Pizza Place   
32      Morris Park           Pizza Place                Bakery   
33          Belmont    Italian Restaurant           Pizza Place   
35  North Riverdale           Pizza Place    Italian Restaurant   
37    Schuylerville           Pizza Place              Pharmacy   
38   Edgewater Park    Italian Restaurant         Deli / Bodega   
39      Castle Hill           Pizza Place         Deli / Bodega   
50         Allerton           Pizza Place         Deli / Bodega   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6                    Pub            Playground     Food & Drink Shop   
10    Frozen Yogurt Shop         Deli / Bodega                Bakery   
16            Restaurant     Mobile Phone Shop         Deli / Bodega   
27             Juice Bar            Sports Bar                   Bar   
31                Bakery            Playground           Coffee Shop   
32         Deli / Bodega          Burger Joint                Buffet   
33         Deli / Bodega                Bakery         Grocery Store   
35                  Bank      Sushi Restaurant            Donut Shop   
37    Mexican Restaurant                 Diner                  Bank   
38           Pizza Place        Ice Cream Shop                   Pub   
39        Cosmetics Shop              Pharmacy                 Diner   
50      Department Store        Cosmetics Shop           Supermarket   

   6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
6      Convenience Store          Liquor Store               Cosmetics Shop   
10        Sandwich Place         Metro Station                         Food   
16    Spanish Restaurant            Shoe Store                         Café   
27      Asian Restaurant           Coffee Shop          American Restaurant   
31            Donut Shop  Caribbean Restaurant                  Bus Station   
32           Supermarket           Coffee Shop                   Donut Shop   
33          Dessert Shop            Donut Shop                         Bank   
35           Bus Station    Mexican Restaurant                  Social Club   
37    Italian Restaurant        Sandwich Place          American Restaurant   
38            Sports Bar    Chinese Restaurant                   Donut Shop   
39                Market                  Bank  Eastern European Restaurant   
50          Dessert Shop        Discount Store           Chinese Restaurant   

   9th Most Common Venue 10th Most Common Venue  
6          Train Station                  Trail  
10                   Spa             Donut Shop  
16           Supermarket                 Lounge  
27    Italian Restaurant                  Diner  
31            Board Shop            Supermarket  
32        Sandwich Place                    Bar  
33           Fish Market         Sandwich Place  
35          Burger Joint               Building  
37     Convenience Store             Hookah Bar  
38          Liquor Store            Coffee Shop  
39           Flower Shop            Fish Market  
50   Fried Chicken Joint   Fast Food Restaurant

#### Cluster 3

In [38]:
bx_merged.loc[bx_merged['Cluster Labels'] == 2, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Neighborhood   1st Most Common Venue      2nd Most Common Venue  \
0            Wakefield                Pharmacy             Ice Cream Shop   
2          Eastchester    Caribbean Restaurant              Deli / Bodega   
5          Kingsbridge             Pizza Place                        Bar   
9           Baychester              Donut Shop       Other Great Outdoors   
13  University Heights     Fried Chicken Joint                Pizza Place   
15             Fordham       Mobile Phone Shop                 Shoe Store   
19             Melrose             Pizza Place                   Pharmacy   
20          Mott Haven             Pizza Place         Spanish Restaurant   
21         Port Morris  Furniture / Home Store  Latin American Restaurant   
22            Longwood           Deli / Bodega  Latin American Restaurant   
24          Morrisania          Discount Store                Pizza Place   
30  Westchester Square    Fast Food Restaurant                Pizza Place   
36          Pelham Bay      Italian Restaurant                       Bank   
40           Olinville    Caribbean Restaurant                Supermarket   
42           Concourse           Grocery Store              Deli / Bodega   
43           Unionport          Ice Cream Shop                 Donut Shop   
46   Concourse Village          Sandwich Place       Fast Food Restaurant   
47          Mount Eden                Pharmacy         Spanish Restaurant   
48          Mount Hope           Grocery Store         Spanish Restaurant   

        3rd Most Common Venue 4th Most Common Venue  \
0                  Laundromat           Gas Station   
2                       Diner              Bus Stop   
5          Mexican Restaurant           Supermarket   
9              Sandwich Place   Fried Chicken Joint   
13         Chinese Restaurant              Pharmacy   
15                       Bank  Gym / Fitness Center   
19       Gym / Fitness Center         Grocery Store   
20                        Gym            Donut Shop   
21         Spanish Restaurant            Restaurant   
22       Fast Food Restaurant            Donut Shop   
24                 Donut Shop  Fast Food Restaurant   
30                   Pharmacy            Donut Shop   
36             Sandwich Place  Fast Food Restaurant   
40        Fried Chicken Joint                  Food   
42         Spanish Restaurant         Metro Station   
43  Latin American Restaurant          Dance Studio   
46              Deli / Bodega           Bus Station   
47                Pizza Place  Fast Food Restaurant   
48           Asian Restaurant        Ice Cream Shop   

        5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Caribbean Restaurant            Donut Shop        Sandwich Place   
2                 Bus Station         Metro Station           Pizza Place   
5   Latin American Restaurant        Sandwich Place                Bakery   
9           Electronics Store                  Bank        Mattress Store   
13                     Bakery            Shoe Store  Fast Food Restaurant   
15         Spanish Restaurant            Donut Shop           Pizza Place   
19             Discount Store        Sandwich Place                 Diner   
20  Latin American Restaurant              Pharmacy        Baseball Field   
21                 Food Truck      Storage Facility        Baseball Field   
22              Grocery Store                  Park        Sandwich Place   
24                Bus Station        Ice Cream Shop         Bowling Alley   
30             Sandwich Place    Spanish Restaurant                  Park   
36       Gym / Fitness Center    Chinese Restaurant            Donut Shop   
40              Metro Station      Basketball Court    Chinese Restaurant   
42                     Bakery  Fast Food Restaurant                  Food   
43                     Lounge           Pizza Place                 Diner   
46         Chinese Restaurant   Sporting Goods Shop   Fried

#### Cluster 4

In [39]:
bx_merged.loc[bx_merged['Cluster Labels'] == 3, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8  Williamsbridge  Caribbean Restaurant     Convenience Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8            Soup Place             Nightclub                   Bar   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8         Women's Store           Flower Shop           Fish Market   

  9th Most Common Venue 10th Most Common Venue  
8     Fish & Chips Shop   Fast Food Restaurant

#### Cluster 5

In [40]:
bx_merged.loc[bx_merged['Cluster Labels'] == 4, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Neighborhood 1st Most Common Venue          2nd Most Common Venue  \
1            Co-op City           Bus Station                     Restaurant   
4             Riverdale                  Park           Medical Supply Store   
7               Norwood           Pizza Place                           Park   
11          City Island       Harbor / Marina                           Park   
12         Bedford Park    Chinese Restaurant                          Diner   
14       Morris Heights    Spanish Restaurant                       Pharmacy   
17           West Farms           Bus Station                           Park   
18         High  Bridge              Pharmacy                    Pizza Place   
23          Hunts Point        Shipping Store                      Juice Bar   
25            Soundview    Chinese Restaurant                  Grocery Store   
26         Clason Point                  Park      South American Restaurant   
28         Country Club        Sandwich Place                     Comic Shop   
29          Parkchester           Supermarket                    Pizza Place   
34       Spuyten Duyvil          Intersection                Thai Restaurant   
41       Pelham Gardens            Donut Shop                       Pharmacy   
44             Edenwald         Grocery Store                    Fish Market   
45    Claremont Village    Chinese Restaurant                  Grocery Store   
49            Bronxdale        Breakfast Spot  Paper / Office Supplies Store   
51  Kingsbridge Heights           Pizza Place             Chinese Restaurant   

   3rd Most Common Venue      4th Most Common Venue  \
1          Grocery Store                   Pharmacy   
4                  Plaza                        Gym   
7          Deli / Bodega                       Bank   
11    Seafood Restaurant     Thrift / Vintage Store   
12           Pizza Place         Mexican Restaurant   
14           Pizza Place          Recreation Center   
17            Playground           Basketball Court   
18           Bus Station         Chinese Restaurant   
23          Gourmet Shop                       Bank   
25        Breakfast Spot  Latin American Restaurant   
26                  Pool               Home Service   
28    Chinese Restaurant                 Playground   
29            Kids Store         Chinese Restaurant   
34                  Park                   Bus Line   
41           Bus Station        American Restaurant   
44           Bus Station                Supermarket   
45                  Park              Deli / Bodega   
49    Spanish Restaurant                Supermarket   
51           Coffee Shop              Grocery Store   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1          Fast Food Restaurant   Fried Chicken Joint        Mattress Store   
4                   Bus Station            Food Truck                  Bank   
7                      Pharmacy           Coffee Shop    Chinese Restaurant   
11               History Museum                   Bar         Deli / Bodega   
12               Sandwich Place         Deli / Bodega    Spanish Restaurant   
14                  Supermarket         Grocery Store                  Bank   
17                       Lounge            Donut Shop                 Diner   
18                  Supermarket         Deli / Bodega        Sandwich Place   
23                Grocery Store             BBQ Joint                  Café   
25                   Playground        Discount Store              Bus Stop   
26                Boat or Ferry              Bus Stop         Grocery Store   
28                 Dessert Shop      Department Store           Fish Market   
29            Mobile Phone Shop   American Restaurant    Italian Restaurant   
34                         Food                  Bank          Tennis Court   
41                         Bank              Bus Line                  Food   
44                  Gas Station             G

#### Visualizing the clusters

In [41]:
# create map
bxmap_clusters = folium.Map(location=[bxlatitude, bxlongitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(bx_merged['Latitude'], bx_merged['Longitude'], bx_merged['Neighborhood'], bx_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(bxmap_clusters)
       
bxmap_clusters

#### Completion of Analysis for Bronx

We have now completed the analysis and clustering for Bronx and this would now help Mr.John take an informed decision if he wishes to relocate to any of the neighborhoods in Bronx.

However our analysis is still not complete. Remember there are other Boroughs in New York and we have not done any analysis on those. We will now proceed to do similar analysis for each of the other Boroughs so that Mr.John has all of the required information to make an informed Decision.

### Let us now proceed onto Queens do similar analysis and clustering of those neighborhoods

Lets now create a new Dataframe which has only Queens neighborhoods

In [42]:
qu_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
qu_data.head(500)

Borough          Neighborhood   Latitude  Longitude
0   Queens               Astoria  40.768509 -73.915654
1   Queens              Woodside  40.746349 -73.901842
2   Queens       Jackson Heights  40.751981 -73.882821
3   Queens              Elmhurst  40.744049 -73.881656
4   Queens          Howard Beach  40.654225 -73.838138
5   Queens                Corona  40.742382 -73.856825
6   Queens          Forest Hills  40.725264 -73.844475
7   Queens           Kew Gardens  40.705179 -73.829819
8   Queens         Richmond Hill  40.697947 -73.831833
9   Queens              Flushing  40.764454 -73.831773
10  Queens      Long Island City  40.750217 -73.939202
11  Queens             Sunnyside  40.740176 -73.926916
12  Queens         East Elmhurst  40.764073 -73.867041
13  Queens               Maspeth  40.725427 -73.896217
14  Queens             Ridgewood  40.708323 -73.901435
15  Queens              Glendale  40.702762 -73.870742
16  Queens             Rego Park  40.728974 -73.857827
17  Queens             Woodhaven  40.689887 -73.858110
18  Queens            Ozone Park  40.680708 -73.843203
19  Queens      South Ozone Park  40.668550 -73.809865
20  Queens         College Point  40.784903 -73.843045
21  Queens            Whitestone  40.781291 -73.814202
22  Queens               Bayside  40.766041 -73.774274
23  Queens            Auburndale  40.761730 -73.791762
24  Queens           Little Neck  40.770826 -73.738898
25  Queens            Douglaston  40.766846 -73.742498
26  Queens             Glen Oaks  40.749441 -73.715481
27  Queens             Bellerose  40.728573 -73.720128
28  Queens     Kew Gardens Hills  40.722578 -73.820878
29  Queens         Fresh Meadows  40.734394 -73.782713
30  Queens             Briarwood  40.710935 -73.811748
31  Queens        Jamaica Center  40.704657 -73.796902
32  Queens       Oakland Gardens  40.745619 -73.754950
33  Queens        Queens Village  40.718893 -73.738715
34  Queens                Hollis  40.711243 -73.759250
35  Queens         South Jamaica  40.696911 -73.790426
36  Queens            St. Albans  40.694445 -73.758676
37  Queens              Rochdale  40.675211 -73.772588
38  Queens   Springfield Gardens  40.666230 -73.760421
39  Queens       Cambria Heights  40.692775 -73.735269
40  Queens              Rosedale  40.659816 -73.735261
41  Queens          Far Rockaway  40.603134 -73.754980
42  Queens         Broad Channel  40.603027 -73.820055
43  Queens          Breezy Point  40.557401 -73.925512
44  Queens              Steinway  40.775923 -73.902290
45  Queens            Beechhurst  40.792781 -73.804365
46  Queens           Bay Terrace  40.782843 -73.776802
47  Queens              Edgemere  40.595642 -73.776133
48  Queens               Arverne  40.589144 -73.791992
49  Queens        Rockaway Beach  40.582802 -73.822361
50  Queens              Neponsit  40.572037 -73.857547
51  Queens           Murray Hill  40.764126 -73.812763
52  Queens           Floral Park  40.741378 -73.708847
53  Queens            Holliswood  40.720957 -73.767142
54  Queens       Jamaica Estates  40.716805 -73.787227
55  Queens       Queensboro Hill  40.744572 -73.825809
56  Queens             Hillcrest  40.723825 -73.797603
57  Queens            Ravenswood  40.761705 -73.931575
58  Queens            Lindenwood  40.663918 -73.849638
59  Queens             Laurelton  40.667884 -73.740256
60  Queens           Lefrak City  40.736075 -73.862525
61  Queens          Belle Harbor  40.576156 -73.854018
62  Queens         Rockaway Park  40.580343 -73.841534
63  Queens            Somerville  40.597711 -73.796648
64  Queens            Brookville  40.660003 -73.751753
65  Queens              Bellaire  40.733014 -73.738892
66  Queens          North Corona  40.754071 -73.857518
67  Queens  Forest Hills Gardens  40.714611 -73.841022
68  Queens         Jamaica Hills  40.711460 -73.796465
69  Queens                Utopia  40.733500 -73.796717
70  Queens               Pomonok  40.734936 -73.804861
71  Queens       Astoria Heights  40.770317

Lets also get the Latitude and Longitude co-ordinates for Queens using the geopy library

In [43]:
address = 'Queens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
qulatitude = location.latitude
qulongitude = location.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(qulatitude, qulongitude))

The geograpical coordinate of Queens are 40.7498243, -73.7976337.


A picture says a thousand words, so lets create a map using Folium and superimpose the Queens data alone

In [44]:
map_qu = folium.Map(location=[qulatitude, qulongitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(qu_data['Latitude'], qu_data['Longitude'], qu_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_qu)  
    
map_qu

Lets reuse the function we created earlier now for Queens but this time around we are going to get the Top 100 venues and within the radius of 500 meters of each neighborhood in Queens

In [45]:
# type your answer here
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

qu_venues = getNearbyVenues(names=qu_data['Neighborhood'],
                                   latitudes=qu_data['Latitude'],
                                   longitudes=qu_data['Longitude']
                                  )

Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


#### Lets check the size of this dataframe

In [46]:
print(qu_venues.shape)
qu_venues.head()

(2091, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0        Favela Grill       40.767348       -73.917897  Brazilian Restaurant  
1      Orange Blossom       40.769856       -73.917012          Gourmet Shop  
2    Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop  
3     CrossFit Queens       40.769404       -73.918977                   Gym  
4  Simply Fit Astoria       40.769114       -73.912403                   Gym

Grouping the Venues by Neighborhood

In [47]:
qu_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                  18                      18     18   
Astoria                                 100                     100    100   
Astoria Heights                          14                      14     14   
Auburndale                               16                      16     16   
Bay Terrace                              39                      39     39   
Bayside                                  74                      74     74   
Bayswater                                 2                       2      2   
Beechhurst                               12                      12     12   
Bellaire                                 12                      12     12   
Belle Harbor                             17                      17     17   
Bellerose                                22                      22     22   
Blissville                               20                      20     20   
Breezy Point                              3                       3      3   
Briarwood                                 9                       9      9   
Broad Channel                             5                       5      5   
Brookville                                1                       1      1   
Cambria Heights                          12                      12     12   
College Point                            35                      35     35   
Corona                                   20                      20     20   
Douglaston                               20                      20     20   
East Elmhurst                             9                       9      9   
Edgemere                                 14                      14     14   
Elmhurst                                 26                      26     26   
Far Rockaway                             31                      31     31   
Floral Park                               7                       7      7   
Flushing                                 61                      61     61   
Forest Hills                             38                      38     38   
Forest Hills Gardens                     24                      24     24   
Fresh Meadows                            15                      15     15   
Glen Oaks                                22                      22     22   
Glendale                                  5                       5      5   
Hammels                                  19                      19     19   
Hillcrest                                18                      18     18   
Hollis                                   15                      15     15   
Holliswood                                5                       5      5   
Howard Beach                             38                      38     38   
Hunters Point                            58                      58     58   
Jackson Heights                          81                      81     81   
Jamaica Center                           44                      44     44   
Jamaica Estates                           2                       2      2   
Jamaica Hills                            26                      26     26   
Kew Gardens                              49                      49     49   
Kew Gardens Hills                        22                      22     22   
Laurelton                                 6                       6      6   
Lefrak City                              24                      24     24   
Lindenwood                               14                      14     14   
Little Neck                              51                      51     51   
Long Island City                         71                      71     71   
Malba                                     4                       4      4   
Maspeth                                  33 

In [48]:
print('There are {} uniques categories.'.format(len(qu_venues['Venue Category'].unique())))

There are 270 uniques categories.


#### Lets analyze each neighborhood in Queens

In [49]:
# one hot encoding
qu_onehot = pd.get_dummies(qu_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
qu_onehot['Neighborhood'] = qu_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [qu_onehot.columns[-1]] + list(qu_onehot.columns[:-1])
qu_onehot = qu_onehot[fixed_columns]

qu_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport Terminal  \
0            0                  0                  0                 0   
1            0                  0                  0                 0   
2            0                  0                  0                 0   
3            0                  0                  0                 0   
4            0                  0                  0                 0   

   American Restaurant  Antique Shop  Arepa Restaurant  \
0                    0             0                 0   
1                    0             0                 0   
2                    0             0                 0   
3                    0             0                 0   
4                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0          0           0       0     0    0               0   
1                0          0           0       0     0    0               0   
2                0          0           0       0     0    0               0   
3                0          0           0       0     0    0               0   
4                0          0           0       0     0    0               0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                 0           0      0          0                0   
1                 0           0      0          0                0   
2                 0           0      0          0                0   
3                 0           0      0          0                0   
4                 0           0      0          0                0   

   Beer Garden  Bike Trail  Bistro  Board Shop  Bookstore  Boutique  \
0            0           0       0           0          0         0   
1            0           0       0           0          0         0   
2            0           0       0           0          0         0   
3            0           0       0           0          0         0   
4            0           0       0           0          0         0   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0              0                     1               0        0            0   
1              0                     0               0        0            0   
2              0                     0               0        0            0   
3              0                     0               0        0            0   
4              0                     0               0        0            0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0         0             0              0         0   
1                0       0         0             0              0         0   
2                0       0         0             0              0         0   
3                0       0         0             0              0         0   
4                0       0         0             0              0         0   

   Bus Station  Bus Stop  Business Service  Butcher  Café  \
0            0       

In [50]:
qu_onehot.shape

(2091, 270)

#### Lets group the rows by Neighborhood and by taking the mean of the frequency of occurance of each category

In [51]:
qu_grouped = qu_onehot.groupby('Neighborhood').mean().reset_index()
qu_grouped

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0                Arverne     0.000000           0.000000           0.000000   
1                Astoria     0.000000           0.000000           0.000000   
2        Astoria Heights     0.000000           0.000000           0.000000   
3             Auburndale     0.000000           0.000000           0.000000   
4            Bay Terrace     0.000000           0.025641           0.000000   
5                Bayside     0.013514           0.000000           0.000000   
6              Bayswater     0.000000           0.000000           0.000000   
7             Beechhurst     0.083333           0.000000           0.000000   
8               Bellaire     0.000000           0.000000           0.000000   
9           Belle Harbor     0.000000           0.000000           0.000000   
10             Bellerose     0.000000           0.000000           0.000000   
11            Blissville     0.000000           0.000000           0.000000   
12          Breezy Point     0.000000           0.000000           0.000000   
13             Briarwood     0.000000           0.000000           0.000000   
14         Broad Channel     0.000000           0.000000           0.000000   
15            Brookville     0.000000           0.000000           0.000000   
16       Cambria Heights     0.000000           0.000000           0.000000   
17         College Point     0.000000           0.000000           0.000000   
18                Corona     0.000000           0.000000           0.000000   
19            Douglaston     0.000000           0.000000           0.000000   
20         East Elmhurst     0.000000           0.000000           0.000000   
21              Edgemere     0.000000           0.000000           0.000000   
22              Elmhurst     0.000000           0.000000           0.000000   
23          Far Rockaway     0.000000           0.000000           0.000000   
24           Floral Park     0.000000           0.000000           0.000000   
25              Flushing     0.016393           0.000000           0.000000   
26          Forest Hills     0.052632           0.000000           0.000000   
27  Forest Hills Gardens     0.000000           0.000000           0.000000   
28         Fresh Meadows     0.000000           0.000000           0.000000   
29             Glen Oaks     0.000000           0.000000           0.000000   
30              Glendale     0.000000           0.000000           0.000000   
31               Hammels     0.000000           0.000000           0.000000   
32             Hillcrest     0.000000           0.000000           0.000000   
33                Hollis     0.000000           0.000000           0.000000   
34            Holliswood     0.000000           0.000000           0.000000   
35          Howard Beach     0.000000           0.000000           0.000000   
36         Hunters Point     0.017241           0.000000           0.000000   
37       Jackson Heights     0.000000           0.000000           0.000000   
38        Jamaica Center     0.000000           0.000000           0.000000   
39       Jamaica Estates     0.000000           0.000000           0.000000   
40         Jamaica Hills     0.000000           0.000000           0.000000   
41           Kew Gardens     0.000000           0.000000           0.000000   
42     Kew Gardens Hills     0.000000           0.000000           0.000000   
43             Laurelton     0.000000           0.000000           0.000000   
44           Lefrak City     0.000000           0.000000           0.000000   
45            Lindenwood     0.000000           0.000000           0.000000   
46           Little Neck     0.000000           0.000000           0.000000   
47      Long Island City     0.000000           0.000000           0.000000   
48                 Malba     0.000000           0.000000           0.000000   
49               Maspeth     0.000000           0.000000      

In [52]:
qu_grouped.shape

(81, 270)

#####  Printing each neighborhood along with the top 5 most common venues

In [53]:
num_top_venues = 5

for hood in qu_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = qu_grouped[qu_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
            venue  freq
0       Surf Spot  0.22
1   Metro Station  0.11
2  Sandwich Place  0.11
3           Beach  0.06
4     Coffee Shop  0.06


----Astoria----
                       venue  freq
0  Middle Eastern Restaurant  0.06
1                        Bar  0.06
2                Pizza Place  0.04
3           Greek Restaurant  0.04
4                 Hookah Bar  0.04


----Astoria Heights----
          venue  freq
0  Burger Joint  0.07
1        Bakery  0.07
2    Laundromat  0.07
3   Supermarket  0.07
4          Food  0.07


----Auburndale----
                  venue  freq
0     Mobile Phone Shop  0.06
1            Hookah Bar  0.06
2        Gymnastics Gym  0.06
3  Fast Food Restaurant  0.06
4          Noodle House  0.06


----Bay Terrace----
                 venue  freq
0       Clothing Store  0.10
1        Women's Store  0.05
2           Donut Shop  0.05
3  American Restaurant  0.05
4    Mobile Phone Shop  0.05


----Bayside----
                 venue  freq
0         

##### Putting this in a pandas dataframe

In [54]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]



Creating a dataframe and displaying the top 10 venues in each neighborhood

In [55]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = qu_grouped['Neighborhood']

for ind in np.arange(qu_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(qu_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
0          Arverne             Surf Spot              Metro Station   
1          Astoria                   Bar  Middle Eastern Restaurant   
2  Astoria Heights                Hostel                     Bakery   
3       Auburndale            Hookah Bar             Discount Store   
4      Bay Terrace        Clothing Store              Women's Store   

      3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0            Sandwich Place             Wine Shop              Playground   
1  Mediterranean Restaurant      Greek Restaurant              Hookah Bar   
2                     Plaza    Chinese Restaurant             Bus Station   
3         Mobile Phone Shop  Fast Food Restaurant  Furniture / Home Store   
4                Shoe Store     Mobile Phone Shop          Lingerie Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Pizza Place                 Beach       Thai Restaurant   
1           Pizza Place    Seafood Restaurant                Bakery   
2         Shopping Mall          Burger Joint                  Food   
3           Supermarket          Noodle House     Korean Restaurant   
4            Kids Store            Donut Shop        Cosmetics Shop   

  9th Most Common Venue 10th Most Common Venue  
0            Board Shop            Coffee Shop  
1                   Pub                   Café  
2           Pizza Place          Bowling Alley  
3    Italian Restaurant     Athletics & Sports  
4   American Restaurant                 Bakery

### Cluster the neighborhoods in Queens using K-Means

In [56]:
# set number of clusters
kclusters = 5

qu_grouped_clustering = qu_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(qu_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 1, 0, 0, 0], dtype=int32)

In [57]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

qu_merged = qu_data

qu_merged = qu_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

qu_merged.head() # check the last columns!

Borough     Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Queens          Astoria  40.768509 -73.915654               0   
1  Queens         Woodside  40.746349 -73.901842               0   
2  Queens  Jackson Heights  40.751981 -73.882821               0   
3  Queens         Elmhurst  40.744049 -73.881656               0   
4  Queens     Howard Beach  40.654225 -73.838138               0   

       1st Most Common Venue      2nd Most Common Venue  \
0                        Bar  Middle Eastern Restaurant   
1              Grocery Store            Thai Restaurant   
2  Latin American Restaurant        Peruvian Restaurant   
3            Thai Restaurant         Mexican Restaurant   
4         Italian Restaurant             Clothing Store   

       3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0   Mediterranean Restaurant       Greek Restaurant            Hookah Bar   
1  Latin American Restaurant                 Bakery   Filipino Restaurant   
2  South American Restaurant                 Bakery       Thai Restaurant   
3  South American Restaurant  Vietnamese Restaurant    Chinese Restaurant   
4                   Pharmacy         Sandwich Place            Bagel Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Pizza Place    Seafood Restaurant                Bakery   
1            Donut Shop                   Bar   American Restaurant   
2     Mobile Phone Shop    Mexican Restaurant         Grocery Store   
3           Pizza Place  Gym / Fitness Center           Snack Place   
4  Fast Food Restaurant          Concert Hall      Tapas Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0                   Pub                   Café  
1                   Pub           Gourmet Shop  
2              Pharmacy                  Diner  
3            Food Court       Malay Restaurant  
4    Mexican Restaurant         Shipping Store

#### Examining the clusters

#### Cluster 1

In [58]:
qu_merged.loc[qu_merged['Cluster Labels'] == 0, qu_merged.columns[[1] + list(range(5, qu_merged.shape[1]))]]

Neighborhood            1st Most Common Venue  \
0                Astoria                              Bar   
1               Woodside                    Grocery Store   
2        Jackson Heights        Latin American Restaurant   
3               Elmhurst                  Thai Restaurant   
4           Howard Beach               Italian Restaurant   
5                 Corona               Mexican Restaurant   
6           Forest Hills             Gym / Fitness Center   
7            Kew Gardens               Chinese Restaurant   
8          Richmond Hill                           Lounge   
9               Flushing                Korean Restaurant   
10      Long Island City                            Hotel   
11             Sunnyside                      Pizza Place   
12         East Elmhurst                       Donut Shop   
13               Maspeth                      Pizza Place   
14             Ridgewood                    Deli / Bodega   
15              Glendale                          Brewery   
16             Rego Park                           Bakery   
17             Woodhaven                    Deli / Bodega   
18            Ozone Park                      Pizza Place   
19      South Ozone Park                             Park   
20         College Point                      Pizza Place   
21            Whitestone                  Bubble Tea Shop   
22               Bayside                              Bar   
23            Auburndale                       Hookah Bar   
24           Little Neck                    Deli / Bodega   
25            Douglaston               Chinese Restaurant   
26             Glen Oaks                         Pharmacy   
27             Bellerose                      Pizza Place   
28     Kew Gardens Hills                             Bank   
29         Fresh Meadows                      Bus Station   
30             Briarwood                    Deli / Bodega   
31        Jamaica Center                Mobile Phone Shop   
32       Oakland Gardens               Chinese Restaurant   
33        Queens Village                             Bank   
34                Hollis                             Park   
35         South Jamaica             Caribbean Restaurant   
36            St. Albans             Caribbean Restaurant   
37              Rochdale  Southern / Soul Food Restaurant   
38   Springfield Gardens                       Donut Shop   
39       Cambria Heights             Caribbean Restaurant   
40              Rosedale                      Bus Station   
41          Far Rockaway                      Pizza Place   
42         Broad Channel              Sporting Goods Shop   
43          Breezy Point                            Beach   
44              Steinway              Rental Car Location   
45            Beechhurst                      Yoga Studio   
46           Bay Terrace                   Clothing Store   
47              Edgemere                      Pizza Place   
48               Arverne                        Surf Spot   
49        Rockaway Beach                            Beach   
51           Murray Hill                Korean Restaurant   
52           Floral Park                Indian Restaurant   
53            Holliswood                       Donut Shop   
55       Queensboro Hill               Chinese Restaurant   
56             Hillcrest                       Donut Shop   
57            Ravenswood               Chinese Restaurant   
58            Lindenwood                           Bakery   
59             Laurelton             Caribbean Restaurant   
60           Lefrak City                 Department Store   
61          Belle Harbor                            Beach   
62         Rockaway Park                            Beach   
65              Bellaire               Chinese Restaurant   
66          North Corona                    Deli / Bodega   
67  Forest Hills Gardens                   Sandwich Place   
68         Jamaica Hills                       

#### Cluster 2

In [59]:
qu_merged.loc[qu_merged['Cluster Labels'] == 1, qu_merged.columns[[1] + list(range(5, qu_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
63   Somerville                  Park         Women's Store   
79    Bayswater                  Park            Playground   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
63                  Farm   Egyptian Restaurant     Electronics Store   
79         Women's Store                  Farm   Egyptian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
63   Empanada Restaurant           Event Space    Falafel Restaurant   
79     Electronics Store   Empanada Restaurant           Event Space   

   9th Most Common Venue 10th Most Common Venue  
63        Farmers Market    Dumpling Restaurant  
79    Falafel Restaurant         Farmers Market

#### Cluster 3

In [60]:
qu_merged.loc[qu_merged['Cluster Labels'] == 2, qu_merged.columns[[1] + list(range(5, qu_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
64   Brookville         Deli / Bodega         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
64        Farmers Market   Egyptian Restaurant     Electronics Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
64   Empanada Restaurant           Event Space    Falafel Restaurant   

   9th Most Common Venue 10th Most Common Venue  
64                  Farm   Fast Food Restaurant

#### Cluster 4

In [61]:
qu_merged.loc[qu_merged['Cluster Labels'] == 3, qu_merged.columns[[1] + list(range(5, qu_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
54  Jamaica Estates     Indian Restaurant          Intersection   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
54         Women's Store        Farmers Market   Egyptian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
54     Electronics Store   Empanada Restaurant           Event Space   

   9th Most Common Venue 10th Most Common Venue  
54    Falafel Restaurant                   Farm

#### Cluster 5

In [62]:
qu_merged.loc[qu_merged['Cluster Labels'] == 4, qu_merged.columns[[1] + list(range(5, qu_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
50     Neponsit                 Beach             Beach Bar   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
50         Women's Store        Farmers Market   Empanada Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
50           Event Space    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
50  Fast Food Restaurant    Egyptian Restaurant

#### Visualizing the clusters

In [63]:
# create map
qumap_clusters = folium.Map(location=[qulatitude, qulongitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(qu_merged['Latitude'], qu_merged['Longitude'], qu_merged['Neighborhood'], qu_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(qumap_clusters)
       
qumap_clusters

#### Completion of Analysis for Queens

We have now completed the analysis and clustering for Queens and this would now help Mr.John take an informed decision if he wishes to relocate to any of the neighborhoods in Queens.

Our analysis of all the 5 Boroughs and its neighborhoods is now complete. 

## Results and Discussion <a name="results"></a>

We have completed our analysis of all the 5 Boroughs and its neighborhoods. Mr.John has not given any preference for any of the Boroughs and we did analysis of all the Boroughs and its neighborhoods.

We now have a 5 clustered set of neighborhoods for each of the Boroughs and **the cluster is formed basis the 10 most common venues in each of the neighborhoods**. Remember Mr.Johns criteria was for a good neighborhood which has good options for restaurants, shopping, schools etc. 

We put this criteria to the fore in our analysis and formed this cluster. By looking at each of these clusters in each of these neighborhoods, Mr.John will now be able to make an informed decision on which neighborhood and Borough he would like to move to.

## Conclusion <a name="conclusion"></a>

Our purpose was to provide John with as much as information about the Neighborhoods and Boroughs in New York with respect to the options they provide so that Mr.John can do a comparision of his existing neighborhood in Toronto to the one that he would like to move to.

I believe we have done just that and provided the options that are available in each of the neighborhood and Borough in New York and did a clustering basis that.

It is now upto Mr.John to make a decision of which neighborhood and Borough he would like to move into. The other factors that Mr.John will also need to consider but not within the purview of this project is the affordability and also the proximity to his workplace.

**Thank You and Hope you enjoyed this analysis**